In [49]:
import pandas as pd
import os
from datetime import datetime, timedelta
import glob
import pandas as pd
import random
import numpy as np
import seaborn as sns
import ast
import json
import os
import re
import itertools
import folium
import hdbscan
import h3
import time

from scipy.spatial.transform import Rotation as R
from scipy.spatial.distance import euclidean
from scipy.spatial.distance import pdist, squareform
import scipy.sparse as sp
from sklearn.cluster import DBSCAN
from sklearn.neighbors import NearestNeighbors
import matplotlib.pyplot as plt
import matplotlib.pylab as pl
import matplotlib.patches as patches
from pydp.algorithms.numerical_mechanisms import LaplaceMechanism
from itertools import combinations
from collections import defaultdict
from collections import Counter
from typing import Dict, Set, List, Optional, Tuple

In [50]:
df_gps = pd.read_csv("C:\\Users\\dmc\\Desktop\\extracted_trips_data.csv")

df_people = pd.read_csv("C:\\Users\\dmc\\Desktop\\individuals_dataset.csv")
df_people = df_people[df_people['GPS_RECORD'] == True]

df_merged = pd.merge(
    df_gps,
    df_people[['ID', 'SEX', 'AGE', 'PRO_CAT', 'WEIGHT_INDIV']],
    left_on='person_id',
    right_on='ID',
    how='inner'
).drop(columns='ID')

h3_resolution = 10

df_merged['start_h3'] = df_merged.apply(lambda row: h3.latlng_to_cell(row['start_lat'], row['start_lon'], h3_resolution), axis=1)
df_merged['end_h3'] = df_merged.apply(lambda row: h3.latlng_to_cell(row['end_lat'], row['end_lon'], h3_resolution), axis=1)

media_peso = df_merged['WEIGHT_INDIV'].mean()

In [51]:
# mode = "SEX"
# mode = "AGE"
mode = "PRO_CAT"

In [52]:
if mode == "SEX":
    df_man = df_merged[df_merged["SEX"] == "Man"]
    df_woman = df_merged[df_merged["SEX"] == "Woman"]
    print("Split fatto per SEX")
    
elif mode == "AGE":
    df_10_19 = df_merged[(df_merged["AGE"] >= 10) & (df_merged["AGE"] <= 19)]
    df_20_29 = df_merged[(df_merged["AGE"] >= 20) & (df_merged["AGE"] <= 29)]
    df_30_39 = df_merged[(df_merged["AGE"] >= 30) & (df_merged["AGE"] <= 39)]
    df_40_49 = df_merged[(df_merged["AGE"] >= 40) & (df_merged["AGE"] <= 49)]
    df_50_59 = df_merged[(df_merged["AGE"] >= 50) & (df_merged["AGE"] <= 59)]
    df_60_69 = df_merged[(df_merged["AGE"] >= 60) & (df_merged["AGE"] <= 69)]
    df_over70 = df_merged[(df_merged["AGE"] >= 70)]
    print("Split fatto per AGE")
    
elif mode == "PRO_CAT":
    df_procat_1 = df_merged[df_merged["PRO_CAT"] == 1]
    df_procat_2 = df_merged[df_merged["PRO_CAT"] == 2]
    df_procat_3 = df_merged[df_merged["PRO_CAT"] == 3]
    df_procat_4 = df_merged[df_merged["PRO_CAT"] == 4]
    df_procat_5 = df_merged[df_merged["PRO_CAT"] == 5]
    df_procat_6 = df_merged[df_merged["PRO_CAT"] == 6]
    df_procat_7 = df_merged[df_merged["PRO_CAT"] == 7]
    df_procat_8 = df_merged[df_merged["PRO_CAT"] == 8]
    print("Split fatto per PRO_CAT")
    
else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

Split fatto per PRO_CAT


In [53]:
if mode == "SEX":
    od_matrix_first_man = df_man.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_man.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_woman = df_woman.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_woman.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

elif mode == "AGE":
    od_matrix_first_10_19 = df_10_19.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_10_19.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_20_29 = df_20_29.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_20_29.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_30_39 = df_30_39.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_30_39.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_40_49 = df_40_49.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_40_49.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_50_59 = df_50_59.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_50_59.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_60_69 = df_60_69.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_60_69.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_over70 = df_over70.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_over70.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

elif mode == "PRO_CAT":
    od_matrix_first_procat_1 = df_procat_1.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_1.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_2 = df_procat_2.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_2.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_3 = df_procat_3.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_3.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_4 = df_procat_4.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_4.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_5 = df_procat_5.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_5.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_6 = df_procat_6.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_6.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_7 = df_procat_7.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_7.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

    od_matrix_first_procat_8 = df_procat_8.groupby(['start_h3', 'end_h3']).agg({'WEIGHT_INDIV': ['sum', 'count']}).reset_index()
    od_matrix_first_procat_8.columns = ['start_h3', 'end_h3', 'total_weight', 'count']

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [54]:
parent_hexes = ["861fb4667ffffff", "861fb4677ffffff", "861fb466fffffff", "861fb4647ffffff", "861fb475fffffff"]

target_resolution = 10
start_valid_h3 = set()
end_valid_h3 = set()

for parent in parent_hexes:
    children = h3.cell_to_children(parent, target_resolution)
    for child in children:
        start_valid_h3.add(child)
        end_valid_h3.add(child)

if mode == "SEX":
    mask_man = ((od_matrix_first_man["start_h3"].isin(start_valid_h3)) & (od_matrix_first_man["end_h3"].isin(end_valid_h3)))
    mask_woman = ((od_matrix_first_woman["start_h3"].isin(start_valid_h3)) & (od_matrix_first_woman["end_h3"].isin(end_valid_h3)))

    od_matrix_first_man = od_matrix_first_man[mask_man].copy()
    od_matrix_first_woman = od_matrix_first_woman[mask_woman].copy()

elif mode == "AGE":
    mask_10_19 = ((od_matrix_first_10_19["start_h3"].isin(start_valid_h3)) & (od_matrix_first_10_19["end_h3"].isin(end_valid_h3)))
    mask_20_29 = ((od_matrix_first_20_29["start_h3"].isin(start_valid_h3)) & (od_matrix_first_20_29["end_h3"].isin(end_valid_h3)))
    mask_30_39 = ((od_matrix_first_30_39["start_h3"].isin(start_valid_h3)) & (od_matrix_first_30_39["end_h3"].isin(end_valid_h3)))
    mask_40_49 = ((od_matrix_first_40_49["start_h3"].isin(start_valid_h3)) & (od_matrix_first_40_49["end_h3"].isin(end_valid_h3)))
    mask_50_59 = ((od_matrix_first_50_59["start_h3"].isin(start_valid_h3)) & (od_matrix_first_50_59["end_h3"].isin(end_valid_h3)))
    mask_60_69 = ((od_matrix_first_60_69["start_h3"].isin(start_valid_h3)) & (od_matrix_first_60_69["end_h3"].isin(end_valid_h3)))
    mask_over70 = ((od_matrix_first_over70["start_h3"].isin(start_valid_h3)) & (od_matrix_first_over70["end_h3"].isin(end_valid_h3)))

    od_matrix_first_10_19 = od_matrix_first_10_19[mask_10_19].copy()
    od_matrix_first_20_29 = od_matrix_first_20_29[mask_20_29].copy()
    od_matrix_first_30_39 = od_matrix_first_30_39[mask_30_39].copy()
    od_matrix_first_40_49 = od_matrix_first_40_49[mask_40_49].copy()
    od_matrix_first_50_59 = od_matrix_first_50_59[mask_50_59].copy()
    od_matrix_first_60_69 = od_matrix_first_60_69[mask_60_69].copy()
    od_matrix_first_over70 = od_matrix_first_over70[mask_over70].copy()

elif mode == "PRO_CAT":
    mask_procat_1 = ((od_matrix_first_procat_1["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_1["end_h3"].isin(end_valid_h3)))
    mask_procat_2 = ((od_matrix_first_procat_2["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_2["end_h3"].isin(end_valid_h3)))
    mask_procat_3 = ((od_matrix_first_procat_3["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_3["end_h3"].isin(end_valid_h3)))
    mask_procat_4 = ((od_matrix_first_procat_4["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_4["end_h3"].isin(end_valid_h3)))
    mask_procat_5 = ((od_matrix_first_procat_5["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_5["end_h3"].isin(end_valid_h3)))
    mask_procat_6 = ((od_matrix_first_procat_6["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_6["end_h3"].isin(end_valid_h3)))
    mask_procat_7 = ((od_matrix_first_procat_7["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_7["end_h3"].isin(end_valid_h3)))
    mask_procat_8 = ((od_matrix_first_procat_8["start_h3"].isin(start_valid_h3)) & (od_matrix_first_procat_8["end_h3"].isin(end_valid_h3)))

    od_matrix_first_procat_1 = od_matrix_first_procat_1[mask_procat_1].copy()
    od_matrix_first_procat_2 = od_matrix_first_procat_2[mask_procat_2].copy()
    od_matrix_first_procat_3 = od_matrix_first_procat_3[mask_procat_3].copy()
    od_matrix_first_procat_4 = od_matrix_first_procat_4[mask_procat_4].copy()
    od_matrix_first_procat_5 = od_matrix_first_procat_5[mask_procat_5].copy()
    od_matrix_first_procat_6 = od_matrix_first_procat_6[mask_procat_6].copy()
    od_matrix_first_procat_7 = od_matrix_first_procat_7[mask_procat_7].copy()
    od_matrix_first_procat_8 = od_matrix_first_procat_8[mask_procat_8].copy()

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [55]:
if mode == "SEX":
    od_matrix_man = od_matrix_first_man.copy()
    od_matrix_woman = od_matrix_first_woman.copy()

elif mode == "AGE":
    od_matrix_10_19 = od_matrix_first_10_19.copy()
    od_matrix_20_29 = od_matrix_first_20_29.copy()
    od_matrix_30_39 = od_matrix_first_30_39.copy()
    od_matrix_40_49 = od_matrix_first_40_49.copy()
    od_matrix_50_59 = od_matrix_first_50_59.copy()
    od_matrix_60_69 = od_matrix_first_60_69.copy()
    od_matrix_over70 = od_matrix_first_over70.copy()

elif mode == "PRO_CAT":
    od_matrix_procat_1 = od_matrix_first_procat_1.copy()
    od_matrix_procat_2 = od_matrix_first_procat_2.copy()
    od_matrix_procat_3 = od_matrix_first_procat_3.copy()
    od_matrix_procat_4 = od_matrix_first_procat_4.copy()
    od_matrix_procat_5 = od_matrix_first_procat_5.copy()
    od_matrix_procat_6 = od_matrix_first_procat_6.copy()
    od_matrix_procat_7 = od_matrix_first_procat_7.copy()
    od_matrix_procat_8 = od_matrix_first_procat_8.copy()

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [56]:
def fast_pre_generalization_filter(
    od_matrix: pd.DataFrame,
    k_threshold: int = 10,
    max_generalization_levels: int = 3,
    suppression_budget_percent: float = 0.1
) -> pd.DataFrame:
    """
    Filtra coppie OD che non riescono a diventare k-anonime nemmeno generalizzando fino al livello massimo,
    usando 'total_weight' come base per il calcolo del k-anonimato.
    
    Args:
        od_matrix: DataFrame con colonne ['start_h3', 'end_h3', 'count', 'total_weight']
        k_threshold: Soglia k-anonimato (basata su total_weight)
        max_generalization_levels: Massimo numero di livelli di generalizzazione consentiti
    
    Returns:
        DataFrame filtrato con colonne ['start_h3', 'end_h3', 'count', 'total_weight']
    """
    print("⚙️ Inizio filtro veloce pre-generalizzazione...")

    original_size = len(od_matrix)
    max_suppressions = int(original_size * suppression_budget_percent)
    print(f"📊 Budget suppression: {max_suppressions} righe su {original_size} ({suppression_budget_percent*100:.1f}%)")

    mapping_cache = {}

    def generalize(h, level_down):
        res = h3.get_resolution(h)
        target_res = res - level_down
        if target_res < 0:
            target_res = 0
        key = (h, target_res)
        if key not in mapping_cache:
            mapping_cache[key] = h3.cell_to_parent(h, target_res) if res > target_res else h
        return mapping_cache[key]

    results = []
    od_working = od_matrix.copy()
    for lvl in range(max_generalization_levels + 1):
        od_working[f'start_gen_{lvl}'] = od_working['start_h3'].apply(lambda x: generalize(x, lvl))
        od_working[f'end_gen_{lvl}'] = od_working['end_h3'].apply(lambda x: generalize(x, lvl))

    for lvl in range(max_generalization_levels + 1):
        grouped = od_working.groupby([f'start_gen_{lvl}', f'end_gen_{lvl}'])['total_weight'].sum().reset_index()
        grouped.columns = ['start_gen', 'end_gen', 'agg_weight']
        grouped['level'] = lvl
        results.append(grouped)

    all_levels = pd.concat(results, ignore_index=True)

    od_with_id = od_working.reset_index().rename(columns={'index': 'row_id'})

    valid_pairs = set()
    for lvl in range(max_generalization_levels + 1):
        merged = od_with_id.merge(
            all_levels[all_levels['level'] == lvl],
            left_on=[f'start_gen_{lvl}', f'end_gen_{lvl}'],
            right_on=['start_gen', 'end_gen'],
            how='left'
        )
        valid = merged[merged['agg_weight'] >= k_threshold*media_peso]
        valid_pairs.update(valid['row_id'].tolist())

    # Identifica righe problematiche (non k-anonime nemmeno con generalizzazione)
    all_row_ids = set(od_with_id['row_id'].tolist())
    problematic_rows = all_row_ids - valid_pairs
    
    print(f"🔍 Righe k-anonime con generalizzazione: {len(valid_pairs)}")
    print(f"⚠️ Righe problematiche: {len(problematic_rows)}")

    # Decidi cosa fare con le righe problematiche
    if len(problematic_rows) <= max_suppressions:
        # Budget sufficiente: sopprime tutte le righe problematiche
        print(f"✅ Budget sufficiente: soppressione di tutte le {len(problematic_rows)} righe problematiche")
        rows_to_keep = valid_pairs
        suppressed_count = len(problematic_rows)
    else:
        # Budget insufficiente: scegli strategicamente cosa sopprimere
        print(f"🎯 Budget insufficiente: sopprimi prima le righe con peso più basso")
        
        # Ottieni info sulle righe problematiche per la strategia di selezione
        problematic_df = od_with_id[od_with_id['row_id'].isin(problematic_rows)].copy()
        
        # Sopprime prima le righe con count più basso
        # nsmallest : return the first n rows with the smallest values in columns
        to_suppress = problematic_df.nsmallest(max_suppressions, 'total_weight')['row_id'].tolist()
        
        # Mantieni righe k-anonime + righe problematiche non soppresse
        rows_to_suppress = set(to_suppress)
        rows_to_keep = valid_pairs | (problematic_rows - rows_to_suppress)
        suppressed_count = len(to_suppress)
        
        print(f"📋 Soppresse {suppressed_count} righe")

    # Ritorna solo le righe valide e con le colonne start_h3, end_h3 e count
    filtered = od_with_id[od_with_id['row_id'].isin(rows_to_keep)].copy()
    filtered = filtered[['start_h3', 'end_h3', 'total_weight', 'count']]

    kept_count = len(filtered)
    
    print(f"📈 Risultati finali:")
    print(f"   • Righe mantenute: {kept_count} / {original_size} ({kept_count/original_size*100:.1f}%)")
    print(f"   • Righe soppresse: {suppressed_count} ({suppressed_count/original_size*100:.1f}%)")
    print(f"   • Budget utilizzato: {suppressed_count} / {max_suppressions}")

    return filtered, suppressed_count

if mode == "SEX":
    od_matrix_man, suppressed_count_man = fast_pre_generalization_filter(od_matrix_man, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_woman, suppressed_count_woman = fast_pre_generalization_filter(od_matrix_woman, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)

elif mode == "AGE":
    od_matrix_10_19, suppressed_count_10_19 = fast_pre_generalization_filter(od_matrix_10_19, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_20_29, suppressed_count_20_29 = fast_pre_generalization_filter(od_matrix_20_29, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_30_39, suppressed_count_30_39 = fast_pre_generalization_filter(od_matrix_30_39, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_40_49, suppressed_count_40_49 = fast_pre_generalization_filter(od_matrix_40_49, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_50_59, suppressed_count_50_59 = fast_pre_generalization_filter(od_matrix_50_59, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_60_69, suppressed_count_60_69 = fast_pre_generalization_filter(od_matrix_60_69, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_over70, suppressed_count_over70 = fast_pre_generalization_filter(od_matrix_over70, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)

elif mode == "PRO_CAT":
    od_matrix_procat_1, suppressed_count_procat_1 = fast_pre_generalization_filter(od_matrix_procat_1, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_procat_2, suppressed_count_procat_2 = fast_pre_generalization_filter(od_matrix_procat_2, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_procat_3, suppressed_count_procat_3 = fast_pre_generalization_filter(od_matrix_procat_3, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_procat_4, suppressed_count_procat_4 = fast_pre_generalization_filter(od_matrix_procat_4, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_procat_5, suppressed_count_procat_5 = fast_pre_generalization_filter(od_matrix_procat_5, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_procat_6, suppressed_count_procat_6 = fast_pre_generalization_filter(od_matrix_procat_6, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_procat_7, suppressed_count_procat_7 = fast_pre_generalization_filter(od_matrix_procat_7, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)
    od_matrix_procat_8, suppressed_count_procat_8 = fast_pre_generalization_filter(od_matrix_procat_8, k_threshold=10, max_generalization_levels=3, suppression_budget_percent=0.1)

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

⚙️ Inizio filtro veloce pre-generalizzazione...
📊 Budget suppression: 99 righe su 997 (10.0%)
🔍 Righe k-anonime con generalizzazione: 579
⚠️ Righe problematiche: 418
🎯 Budget insufficiente: sopprimi prima le righe con peso più basso
📋 Soppresse 99 righe
📈 Risultati finali:
   • Righe mantenute: 898 / 997 (90.1%)
   • Righe soppresse: 99 (9.9%)
   • Budget utilizzato: 99 / 99
⚙️ Inizio filtro veloce pre-generalizzazione...
📊 Budget suppression: 856 righe su 8569 (10.0%)
🔍 Righe k-anonime con generalizzazione: 7094
⚠️ Righe problematiche: 1475
🎯 Budget insufficiente: sopprimi prima le righe con peso più basso
📋 Soppresse 856 righe
📈 Risultati finali:
   • Righe mantenute: 7713 / 8569 (90.0%)
   • Righe soppresse: 856 (10.0%)
   • Budget utilizzato: 856 / 856
⚙️ Inizio filtro veloce pre-generalizzazione...
📊 Budget suppression: 379 righe su 3795 (10.0%)
🔍 Righe k-anonime con generalizzazione: 3032
⚠️ Righe problematiche: 763
🎯 Budget insufficiente: sopprimi prima le righe con peso più bas

In [57]:
if mode == "SEX":
    filtered_df_man = df_merged.merge(od_matrix_man[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_woman = df_merged.merge(od_matrix_woman[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')

elif mode == "AGE":
    filtered_df_10_19 = df_merged.merge(od_matrix_10_19[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_20_29 = df_merged.merge(od_matrix_20_29[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_30_39 = df_merged.merge(od_matrix_30_39[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_40_49 = df_merged.merge(od_matrix_40_49[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_50_59 = df_merged.merge(od_matrix_50_59[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_60_69 = df_merged.merge(od_matrix_60_69[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_over70 = df_merged.merge(od_matrix_over70[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')

elif mode == "PRO_CAT":
    filtered_df_procat_1 = df_merged.merge(od_matrix_procat_1[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_2 = df_merged.merge(od_matrix_procat_2[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_3 = df_merged.merge(od_matrix_procat_3[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_4 = df_merged.merge(od_matrix_procat_4[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_5 = df_merged.merge(od_matrix_procat_5[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_6 = df_merged.merge(od_matrix_procat_6[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_7 = df_merged.merge(od_matrix_procat_7[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')
    filtered_df_procat_8 = df_merged.merge(od_matrix_procat_8[['start_h3', 'end_h3']], on=['start_h3', 'end_h3'], how='inner')

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

In [58]:
class H3TreeNode:
    """Nodo dell'albero gerarchico H3"""
    def __init__(self, h3_id: str, resolution: int, total_weight: int = 0, count: int = 0):
        self.h3_id = h3_id
        self.resolution = resolution
        self.total_weight = total_weight
        self.count = count
        self.children: Dict[str, 'H3TreeNode'] = {}
        self.parent: Optional['H3TreeNode'] = None
    
    def add_child(self, child: 'H3TreeNode'):
        """Aggiunge un figlio al nodo"""
        self.children[child.h3_id] = child
        child.parent = self
    
    def add_weight(self, weight: int):
        self.total_weight += weight
        if self.parent:
            self.parent.add_weight(weight)
    
    def add_count(self, count: int):
        self.count += count
        if self.parent:
            self.parent.add_count(count)
    
    def __repr__(self):
        return (f"H3Node(id={self.h3_id}, res={self.resolution}, "
                f"total_weight={self.total_weight}, count={self.count}, children={len(self.children)})")

class H3HierarchicalTree:
    def __init__(self, od_matrix: pd.DataFrame, target_resolution: int = 11, hex_column: str = 'start_h3'):
        self.od_matrix = od_matrix
        self.target_resolution = target_resolution
        self.hex_column = hex_column  # 'start_h3' o 'end_h3'
        self.nodes: Dict[str, H3TreeNode] = {}
        self.root = None
        self.min_resolution = None  # Sarà calcolato dinamicamente
        
    def get_all_hexagons(self) -> Set[str]:
        """Estrae tutti gli esagoni unici dalla colonna specificata"""
        return set(self.od_matrix[self.hex_column].unique())
    
    def get_resolution_coverage(self, hexagons: Set[str], target_res: int) -> Set[str]:
        """
        Ottiene tutti gli esagoni di risoluzione target che coprono l'area
        definita dagli esagoni di input
        """
        coverage_hexagons = set()
        
        for hex_id in hexagons:
            current_res = h3.get_resolution(hex_id)
            
            if current_res == target_res:
                coverage_hexagons.add(hex_id)
            elif current_res < target_res:
                # Dobbiamo espandere a risoluzione più alta
                children = self._get_all_children_at_resolution(hex_id, target_res)
                coverage_hexagons.update(children)
            else:
                # Dobbiamo salire a risoluzione più bassa
                parent = h3.cell_to_parent(hex_id, target_res)
                coverage_hexagons.add(parent)
        
        return coverage_hexagons
    
    def find_optimal_min_resolution(self, hexagons: Set[str]) -> int:
        """
        Trova la risoluzione più alta dove c'è ancora un solo nodo che copre tutti gli esagoni
        """
        print("🔍 Analizzando risoluzione ottimale per radice...")
        
        # Per ogni risoluzione da 0 alla target, conta quanti nodi servono per coprire tutti gli esagoni
        resolution_stats = {}
        
        for resolution in range(0, self.target_resolution + 1):
            ancestors = set()
            for hex_id in hexagons:
                current_res = h3.get_resolution(hex_id)
                if current_res >= resolution:
                    ancestor = h3.cell_to_parent(hex_id, resolution)
                    ancestors.add(ancestor)
                else:
                    # L'esagono è già a risoluzione più bassa, aggiungi direttamente
                    ancestors.add(hex_id)
            
            resolution_stats[resolution] = len(ancestors)
            print(f"  - Risoluzione {resolution}: {len(ancestors)} nodi")
        
        # Trova la risoluzione più alta con count = 1
        optimal_resolution = 0
        for resolution in range(self.target_resolution, -1, -1):
            if resolution_stats[resolution] == 1:
                optimal_resolution = resolution
                break
        
        print(f"✅ Risoluzione ottimale trovata: {optimal_resolution}")
        return optimal_resolution
    
    def get_siblings(self, node_id: str) -> List[str]:
        """Restituisce gli h3_id dei nodi fratelli di node_id (stesso genitore, escluso node_id stesso)"""
        if node_id not in self.nodes:
            return []

        node = self.nodes[node_id]
        parent = node.parent
        if parent is None:
            # Nodo root, non ha fratelli
            return []

        siblings = [child.h3_id for child in parent.children.values() if child.h3_id != node_id]
        return siblings
    
    def get_parent(self, node_id: str) -> Optional[str]:
        """Restituisce l'h3_id del genitore del nodo dato, o None se root o nodo non trovato"""
        if node_id not in self.nodes:
            return None
        node = self.nodes[node_id]
        if node.parent is None:
            return None
        return node.parent.h3_id
    
    def _get_all_children_at_resolution(self, hex_id: str, target_res: int) -> Set[str]:
        """Ricorsivamente ottiene tutti i figli a una risoluzione specifica"""
        current_res = h3.get_resolution(hex_id)
        
        if current_res == target_res:
            return {hex_id}
        elif current_res > target_res:
            # Non dovrebbe succedere in questo contesto
            return set()
        
        children = set()
        direct_children = h3.cell_to_children(hex_id, current_res + 1)
        
        for child in direct_children:
            children.update(self._get_all_children_at_resolution(child, target_res))
        
        return children
    
    def build_hierarchy_path(self, hex_id: str, min_resolution: int) -> List[str]:
        """Costruisce il percorso gerarchico da un esagono fino alla risoluzione minima"""
        path = [hex_id]
        current = hex_id
        current_res = h3.get_resolution(current)
        
        while current_res > min_resolution:
            parent = h3.cell_to_parent(current, current_res - 1)
            path.append(parent)
            current = parent
            current_res -= 1
        
        return path
    
    def create_tree_structure(self):
        """Crea la struttura dell'albero ottimizzato"""
        target_hexagons = self.get_all_hexagons()
        
        # Ottieni copertura completa alla risoluzione target
        coverage_hexagons = self.get_resolution_coverage(target_hexagons, self.target_resolution)
        
        # Trova la risoluzione minima ottimale (quella più alta con count=1)
        self.min_resolution = self.find_optimal_min_resolution(coverage_hexagons)
        
        print(f"🏗️ Costruendo albero da risoluzione {self.min_resolution} a {self.target_resolution}")
        
        # Costruisci tutti i percorsi gerarchici
        all_paths = []
        for hex_id in coverage_hexagons:
            path = self.build_hierarchy_path(hex_id, self.min_resolution)
            all_paths.append(path)
        
        # Crea tutti i nodi
        for path in all_paths:
            for hex_id in path:
                if hex_id not in self.nodes:
                    resolution = h3.get_resolution(hex_id)
                    self.nodes[hex_id] = H3TreeNode(hex_id, resolution)
        
        # Stabilisci relazioni parent-child
        for path in all_paths:
            for i in range(len(path) - 1):
                child_id = path[i]
                parent_id = path[i + 1]
                self.nodes[parent_id].add_child(self.nodes[child_id])
        
        # Identifica la radice
        self.root = self.nodes[self._find_root_hexagon(coverage_hexagons, self.min_resolution)]
        
        return self
    
    def _find_root_hexagon(self, hexagons: Set[str], min_resolution: int) -> str:
        """Trova l'esagono radice che contiene tutti gli altri"""
        sample_hex = next(iter(hexagons))
        return h3.cell_to_parent(sample_hex, min_resolution)
    
    def populate_counts(self):
        # Raggruppa per esagono le due metriche
        agg_df = self.od_matrix.groupby(self.hex_column).agg({'total_weight': 'sum', 'count': 'sum'}).reset_index()
        
        for _, row in agg_df.iterrows():
            hex_id = row[self.hex_column]
            weight = int(row['total_weight'])
            count = int(row['count'])
            
            target_hex = self._map_to_target_resolution(hex_id)
            
            if target_hex in self.nodes:
                self.nodes[target_hex].add_weight(weight)
                self.nodes[target_hex].add_count(count)
            else:
                print(f"⚠️ Avviso: esagono {target_hex} non trovato nell'albero")
        
        return self
    
    def _map_to_target_resolution(self, hex_id: str) -> str:
        """Mappa un esagono alla risoluzione target"""
        current_res = h3.get_resolution(hex_id)
        
        if current_res == self.target_resolution:
            return hex_id
        elif current_res < self.target_resolution:
            # Prendi il primo figlio disponibile (potrebbe essere migliorato)
            children = self._get_all_children_at_resolution(hex_id, self.target_resolution)
            return next(iter(children)) if children else hex_id
        else:
            return h3.cell_to_parent(hex_id, self.target_resolution)
    
    def get_tree_statistics(self) -> Dict:
        """Ottiene statistiche dell'albero"""
        if not self.root:
            return {}
        
        stats = {
            'total_nodes': len(self.nodes),
            'root_resolution': self.root.resolution,
            'min_resolution': self.min_resolution,
            'target_resolution': self.target_resolution,
            'total_weight': self.root.total_weight,
            'nodes_by_resolution': defaultdict(int),
            'resolution_range': f"{self.min_resolution} → {self.target_resolution}"
        }
        
        for node in self.nodes.values():
            stats['nodes_by_resolution'][node.resolution] += 1
        
        return stats
    
    def print_tree(self, max_children_per_level: int = 10):
        if not self.root:
            print("❌ Albero non costruito")
            return
        
        print(f"\n🌳 STRUTTURA ALBERO OTTIMIZZATA")
        print(f"📏 Range risoluzione: {self.min_resolution} → {self.target_resolution}")
        print("=" * 80)
        
        def _print_node(node: H3TreeNode, depth: int = 0, is_last: bool = True, prefix: str = ""):
            connector = "└─ " if is_last else "├─ "
            print(f"{prefix}{connector}{node.h3_id} (res:{node.resolution}, total_weight:{node.total_weight}, count:{node.count}, children:{len(node.children)})")
            
            if is_last:
                child_prefix = prefix + "   "
            else:
                child_prefix = prefix + "│  "
            
            children_list = list(node.children.values())
            
            if len(children_list) <= max_children_per_level:
                for i, child in enumerate(children_list):
                    is_last_child = (i == len(children_list) - 1)
                    _print_node(child, depth + 1, is_last_child, child_prefix)
            else:
                for i in range(max_children_per_level):
                    child = children_list[i]
                    is_last_child = (i == max_children_per_level - 1) and (len(children_list) == max_children_per_level)
                    _print_node(child, depth + 1, is_last_child, child_prefix)
                
                remaining = len(children_list) - max_children_per_level
                print(f"{child_prefix}└─ ... e altri {remaining} figli con stesso pattern")
        
        _print_node(self.root, 0, True, "")

def create_h3_hierarchical_tree(od_matrix_df: pd.DataFrame, target_resolution: int = 10, hex_column: str = 'start_h3'):
    """
    Crea un albero gerarchico H3 ottimizzato dal dataset OD matrix
    
    Args:
        od_matrix_df: DataFrame con colonne 'start_h3', 'end_h3', 'count'
        target_resolution: Risoluzione target per le foglie dell'albero
        hex_column: Colonna da analizzare ('start_h3' o 'end_h3')
    
    Returns:
        H3HierarchicalTree: Albero gerarchico costruito e ottimizzato
    """
    
    tree = H3HierarchicalTree(od_matrix_df, target_resolution, hex_column)
    tree.create_tree_structure()
    tree.populate_counts()
    
    stats = tree.get_tree_statistics()
    print(f"\n📈 STATISTICHE ALBERO OTTIMIZZATO ({hex_column.upper()})")
    print("=" * 50)
    print(f"• Nodi totali: {stats['total_nodes']:,}")
    print(f"• Range risoluzione: {stats['resolution_range']}")
    print(f"• Risoluzione radice: {stats['root_resolution']}")
    print(f"• Risoluzione foglie: {stats['target_resolution']}")
    print(f"• Nodi per risoluzione:")
    for res in sorted(stats['nodes_by_resolution'].keys()):
        print(f"  - Risoluzione {res}: {stats['nodes_by_resolution'][res]:,} nodi")
    
    # Calcola risparmio in nodi
    total_resolutions_possible = target_resolution + 1  # da 0 a target
    resolutions_used = len(stats['nodes_by_resolution'])
    resolutions_saved = total_resolutions_possible - resolutions_used
    
    print(f"\n💡 OTTIMIZZAZIONI:")
    print(f"• Risoluzioni risparmiate: {resolutions_saved}")
    print(f"• Efficienza albero: {resolutions_used}/{total_resolutions_possible} livelli utilizzati")
    
    tree.print_tree()
    
    return tree

In [59]:
if mode == "SEX":
    tree_start_man = create_h3_hierarchical_tree(od_matrix_man, target_resolution=10, hex_column='start_h3')
    tree_start_woman = create_h3_hierarchical_tree(od_matrix_woman, target_resolution=10, hex_column='start_h3')

    tree_end_man = create_h3_hierarchical_tree(od_matrix_man, target_resolution=10, hex_column='end_h3')
    tree_end_woman = create_h3_hierarchical_tree(od_matrix_woman, target_resolution=10, hex_column='end_h3')

elif mode == "AGE":
    tree_start_10_19 = create_h3_hierarchical_tree(od_matrix_10_19, target_resolution=10, hex_column='start_h3')
    tree_start_20_29 = create_h3_hierarchical_tree(od_matrix_20_29, target_resolution=10, hex_column='start_h3')
    tree_start_30_39 = create_h3_hierarchical_tree(od_matrix_30_39, target_resolution=10, hex_column='start_h3')
    tree_start_40_49 = create_h3_hierarchical_tree(od_matrix_40_49, target_resolution=10, hex_column='start_h3')
    tree_start_50_59 = create_h3_hierarchical_tree(od_matrix_50_59, target_resolution=10, hex_column='start_h3')
    tree_start_60_69 = create_h3_hierarchical_tree(od_matrix_60_69, target_resolution=10, hex_column='start_h3')
    tree_start_over70 = create_h3_hierarchical_tree(od_matrix_over70, target_resolution=10, hex_column='start_h3')

    tree_end_10_19 = create_h3_hierarchical_tree(od_matrix_10_19, target_resolution=10, hex_column='end_h3')
    tree_end_20_29 = create_h3_hierarchical_tree(od_matrix_20_29, target_resolution=10, hex_column='end_h3')
    tree_end_30_39 = create_h3_hierarchical_tree(od_matrix_30_39, target_resolution=10, hex_column='end_h3')
    tree_end_40_49 = create_h3_hierarchical_tree(od_matrix_40_49, target_resolution=10, hex_column='end_h3')
    tree_end_50_59 = create_h3_hierarchical_tree(od_matrix_50_59, target_resolution=10, hex_column='end_h3')
    tree_end_60_69 = create_h3_hierarchical_tree(od_matrix_60_69, target_resolution=10, hex_column='end_h3')
    tree_end_over70 = create_h3_hierarchical_tree(od_matrix_over70, target_resolution=10, hex_column='end_h3')

elif mode == "PRO_CAT":
    tree_start_procat_1 = create_h3_hierarchical_tree(od_matrix_procat_1, target_resolution=10, hex_column='start_h3')
    tree_start_procat_2 = create_h3_hierarchical_tree(od_matrix_procat_2, target_resolution=10, hex_column='start_h3')
    tree_start_procat_3 = create_h3_hierarchical_tree(od_matrix_procat_3, target_resolution=10, hex_column='start_h3')
    tree_start_procat_4 = create_h3_hierarchical_tree(od_matrix_procat_4, target_resolution=10, hex_column='start_h3')
    tree_start_procat_5 = create_h3_hierarchical_tree(od_matrix_procat_5, target_resolution=10, hex_column='start_h3')
    tree_start_procat_6 = create_h3_hierarchical_tree(od_matrix_procat_6, target_resolution=10, hex_column='start_h3')
    tree_start_procat_7 = create_h3_hierarchical_tree(od_matrix_procat_7, target_resolution=10, hex_column='start_h3')
    tree_start_procat_8 = create_h3_hierarchical_tree(od_matrix_procat_8, target_resolution=10, hex_column='start_h3')

    tree_end_procat_1 = create_h3_hierarchical_tree(od_matrix_procat_1, target_resolution=10, hex_column='end_h3')
    tree_end_procat_2 = create_h3_hierarchical_tree(od_matrix_procat_2, target_resolution=10, hex_column='end_h3')
    tree_end_procat_3 = create_h3_hierarchical_tree(od_matrix_procat_3, target_resolution=10, hex_column='end_h3')
    tree_end_procat_4 = create_h3_hierarchical_tree(od_matrix_procat_4, target_resolution=10, hex_column='end_h3')
    tree_end_procat_5 = create_h3_hierarchical_tree(od_matrix_procat_5, target_resolution=10, hex_column='end_h3')
    tree_end_procat_6 = create_h3_hierarchical_tree(od_matrix_procat_6, target_resolution=10, hex_column='end_h3')
    tree_end_procat_7 = create_h3_hierarchical_tree(od_matrix_procat_7, target_resolution=10, hex_column='end_h3')
    tree_end_procat_8 = create_h3_hierarchical_tree(od_matrix_procat_8, target_resolution=10, hex_column='end_h3')

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

🔍 Analizzando risoluzione ottimale per radice...
  - Risoluzione 0: 1 nodi
  - Risoluzione 1: 1 nodi
  - Risoluzione 2: 1 nodi
  - Risoluzione 3: 1 nodi
  - Risoluzione 4: 1 nodi
  - Risoluzione 5: 2 nodi
  - Risoluzione 6: 5 nodi
  - Risoluzione 7: 33 nodi
  - Risoluzione 8: 140 nodi
  - Risoluzione 9: 392 nodi
  - Risoluzione 10: 631 nodi
✅ Risoluzione ottimale trovata: 4
🏗️ Costruendo albero da risoluzione 4 a 10

📈 STATISTICHE ALBERO OTTIMIZZATO (START_H3)
• Nodi totali: 1,204
• Range risoluzione: 4 → 10
• Risoluzione radice: 4
• Risoluzione foglie: 10
• Nodi per risoluzione:
  - Risoluzione 4: 1 nodi
  - Risoluzione 5: 2 nodi
  - Risoluzione 6: 5 nodi
  - Risoluzione 7: 33 nodi
  - Risoluzione 8: 140 nodi
  - Risoluzione 9: 392 nodi
  - Risoluzione 10: 631 nodi

💡 OTTIMIZZAZIONI:
• Risoluzioni risparmiate: 4
• Efficienza albero: 7/11 livelli utilizzati

🌳 STRUTTURA ALBERO OTTIMIZZATA
📏 Range risoluzione: 4 → 10
└─ 841fb47ffffffff (res:4, total_weight:2301374, count:986, children:2

In [60]:
class OptimizedH3GeneralizedODMatrix:
    """
    Versione ottimizzata per matrici OD molto grandi con conservazione dei count
    """
    
    def __init__(self, od_matrix: pd.DataFrame, tree_start, tree_end, k_threshold: int = 10*media_peso):
        self.original_od_matrix = od_matrix
        self.tree_start = tree_start
        self.tree_end = tree_end
        self.k_threshold = k_threshold
        
        # Usa matrici sparse separate per pesi e conteggi
        self.current_matrix_sparse = None
        self.current_counts_sparse = None
        
        # Mappature ottimizzate
        self.start_to_idx = {}  # {h3_id: index}
        self.end_to_idx = {}    # {h3_id: index}
        self.idx_to_start = {}  # {index: h3_id}
        self.idx_to_end = {}    # {index: h3_id}
        
        # Cache per evitare ricalcoli
        self.sibling_groups_cache = {}
        self.parent_cache = {}
        
        # Storia delle generalizzazioni
        self.generalization_history = []
        
    def initialize_optimized_matrix(self):
        """Inizializza usando matrici sparse e pre-processing intelligente"""
        print("🔧 Inizializzazione ottimizzata...")
        
        # 1. Pre-filtra i dati: rimuovi celle con count = 0
        non_zero_od = self.original_od_matrix[self.original_od_matrix['total_weight'] > 0].copy()
        print(f"📊 Dati filtrati: {len(non_zero_od):,} celle non-zero su {len(self.original_od_matrix):,}")
        
        # 2. Ottieni solo gli esagoni effettivamente utilizzati
        used_starts = set(non_zero_od['start_h3'].unique())
        used_ends = set(non_zero_od['end_h3'].unique())
        
        # 3. Mappa a risoluzione target solo gli esagoni utilizzati
        target_starts = self._get_target_resolution_hexagons(used_starts, self.tree_start)
        target_ends = self._get_target_resolution_hexagons(used_ends, self.tree_end)
        
        print(f"🎯 Esagoni target: {len(target_starts)} origini, {len(target_ends)} destinazioni")
        
        # 4. Crea mappature indicizzate
        self.start_to_idx = {h3_id: idx for idx, h3_id in enumerate(sorted(target_starts))}
        self.end_to_idx = {h3_id: idx for idx, h3_id in enumerate(sorted(target_ends))}
        self.idx_to_start = {idx: h3_id for h3_id, idx in self.start_to_idx.items()}
        self.idx_to_end = {idx: h3_id for h3_id, idx in self.end_to_idx.items()}
        
        # 5. Costruisci matrici sparse separate per pesi e conteggi
        self.current_matrix_sparse, self.current_counts_sparse = self._build_sparse_matrices(
            non_zero_od, target_starts, target_ends
        )
        
        # 6. Pre-calcola i gruppi di siblings
        self._precompute_sibling_groups()
        
        print(f"✅ Matrici sparse inizializzate: {self.current_matrix_sparse.shape} "
              f"({self.current_matrix_sparse.nnz:,} elementi non-zero)")
        
        return self
    
    def _get_target_resolution_hexagons(self, hexagons: Set[str], tree) -> Set[str]:
        """Ottiene esagoni target risoluzione solo per quelli utilizzati"""
        target_hexagons = set()
        target_res = tree.target_resolution
        
        for hex_id in hexagons:
            current_res = h3.get_resolution(hex_id)
            
            if current_res == target_res:
                target_hexagons.add(hex_id)
            elif current_res < target_res:
                # Espandi solo se è nei nodi dell'albero
                if hex_id in tree.nodes:
                    children = self._get_children_at_resolution_fast(hex_id, target_res)
                    target_hexagons.update(children)
            else:
                parent = h3.cell_to_parent(hex_id, target_res)
                target_hexagons.add(parent)
        
        return target_hexagons
    
    def _get_children_at_resolution_fast(self, hex_id: str, target_res: int) -> Set[str]:
        """Versione veloce per ottenere figli"""
        current_res = h3.get_resolution(hex_id)
        if current_res == target_res:
            return {hex_id}
        
        # Usa cache se disponibile
        cache_key = (hex_id, target_res)
        if cache_key in self.sibling_groups_cache:
            return self.sibling_groups_cache[cache_key]
        
        children = set()
        queue = [hex_id]
        
        while queue:
            current = queue.pop(0)
            current_r = h3.get_resolution(current)
            
            if current_r == target_res:
                children.add(current)
            elif current_r < target_res:
                direct_children = h3.cell_to_children(current, current_r + 1)
                queue.extend(direct_children)
        
        self.sibling_groups_cache[cache_key] = children
        return children
    
    def _build_sparse_matrices(self, od_data: pd.DataFrame, target_starts: Set[str], target_ends: Set[str]) -> Tuple[sp.csr_matrix, sp.csr_matrix]:
        """Costruisce matrici sparse separate per pesi e conteggi"""
        rows_weights, cols_weights, data_weights = [], [], []
        rows_counts, cols_counts, data_counts = [], [], []
        
        print("🔨 Costruzione matrici sparse...")
        
        # Raggruppa i dati per efficienza - somma sia pesi che conteggi
        grouped = od_data.groupby(['start_h3', 'end_h3']).agg({
            'total_weight': 'sum',
            'count': 'sum'
        }).reset_index()
        
        for _, row in grouped.iterrows():
            start_h3 = row['start_h3']
            end_h3 = row['end_h3']
            weight = row['total_weight']
            count = row['count']
            
            # Mappa agli esagoni target
            mapped_start = self._map_to_target_fast(start_h3, target_starts, self.tree_start)
            mapped_end = self._map_to_target_fast(end_h3, target_ends, self.tree_end)
            
            if mapped_start and mapped_end:
                start_idx = self.start_to_idx[mapped_start]
                end_idx = self.end_to_idx[mapped_end]
                
                # Aggiungi ai dati per entrambe le matrici
                rows_weights.append(end_idx)
                cols_weights.append(start_idx)
                data_weights.append(weight)
                
                rows_counts.append(end_idx)
                cols_counts.append(start_idx)
                data_counts.append(count)
        
        # Crea matrici sparse COO e converti in CSR
        shape = (len(target_ends), len(target_starts))
        
        # Matrice dei pesi
        matrix_weights_coo = sp.coo_matrix((data_weights, (rows_weights, cols_weights)), shape=shape)
        matrix_weights_csr = matrix_weights_coo.tocsr()
        matrix_weights_csr.sum_duplicates()
        
        # Matrice dei conteggi
        matrix_counts_coo = sp.coo_matrix((data_counts, (rows_counts, cols_counts)), shape=shape)
        matrix_counts_csr = matrix_counts_coo.tocsr()
        matrix_counts_csr.sum_duplicates()
        
        return matrix_weights_csr, matrix_counts_csr
    
    def _map_to_target_fast(self, h3_id: str, target_nodes: Set[str], tree) -> Optional[str]:
        """Versione veloce di mapping con cache"""
        if h3_id in target_nodes:
            return h3_id
        
        # Usa cache
        if h3_id in self.parent_cache:
            cached_parent = self.parent_cache[h3_id]
            if cached_parent in target_nodes:
                return cached_parent
        
        # Calcola mapping
        current_res = h3.get_resolution(h3_id)
        target_res = tree.target_resolution
        
        if current_res > target_res:
            parent = h3.cell_to_parent(h3_id, target_res)
            self.parent_cache[h3_id] = parent
            return parent if parent in target_nodes else None
        elif current_res < target_res:
            # Trova il primo target che contiene questo esagono
            for target in target_nodes:
                if self._is_descendant_fast(target, h3_id):
                    return target
        
        return None
    
    def _is_descendant_fast(self, child_h3: str, parent_h3: str) -> bool:
        """Versione ottimizzata di controllo discendenza"""
        child_res = h3.get_resolution(child_h3)
        parent_res = h3.get_resolution(parent_h3)
        
        if parent_res >= child_res:
            return False
        
        # Cache check
        cache_key = (child_h3, parent_h3)
        if cache_key in self.parent_cache:
            return self.parent_cache[cache_key]
        
        # Calcola
        current = child_h3
        while h3.get_resolution(current) > parent_res:
            current = h3.cell_to_parent(current, h3.get_resolution(current) - 1)
        
        result = current == parent_h3
        self.parent_cache[cache_key] = result
        return result
    
    def _precompute_sibling_groups(self):
        """Pre-calcola tutti i gruppi di siblings possibili"""
        print("🧠 Pre-calcolo gruppi siblings...")
        
        self.start_sibling_groups = self._compute_sibling_groups(self.start_to_idx.keys(), self.tree_start)
        self.end_sibling_groups = self._compute_sibling_groups(self.end_to_idx.keys(), self.tree_end)
        
        print(f"📋 Trovati {len(self.start_sibling_groups)} gruppi origine, {len(self.end_sibling_groups)} gruppi destinazione")
    
    def _compute_sibling_groups(self, nodes: Set[str], tree) -> List[Tuple[List[str], str]]:
        """Calcola tutti i gruppi di siblings una volta sola - INCLUDE figli unici"""
        groups = []
        processed = set()
        
        for node_id in nodes:
            if node_id in processed or node_id not in tree.nodes:
                continue
            
            node = tree.nodes[node_id]
            if not node.parent:
                continue
            
            # Trova tutti i siblings (anche se è uno solo)
            siblings = []
            for sibling_id in node.parent.children:
                if sibling_id in nodes and sibling_id not in processed:
                    siblings.append(sibling_id)
            
            if len(siblings) >= 1:  # Accetta anche figli unici
                groups.append((siblings, node.parent.h3_id))
                processed.update(siblings)
        
        return groups
    
    def get_best_generalization_fast(self, axis: str) -> Optional[Tuple[List[str], str, int]]:
        """Trova la migliore generalizzazione - INCLUDE figli unici"""
        if axis == 'columns':
            tree = self.tree_start
            mapping = self.start_to_idx
            matrix = self.current_matrix_sparse.tocsc()
        else:
            tree = self.tree_end
            mapping = self.end_to_idx
            matrix = self.current_matrix_sparse.tocsr()

        best_group, best_parent, best_cost = None, None, float('inf')
        
        for parent_id, parent_node in tree.nodes.items():
            siblings = list(parent_node.children.keys())
            
            if len(siblings) < 1:  # Solo se non ha figli
                continue
                
            # Filtra solo i siblings ancora presenti nella matrice
            present = [s for s in siblings if s in mapping]
            
            # MODIFICA IMPORTANTE: non richiedere che TUTTI i siblings siano presenti
            # per figli unici, basta che il figlio sia presente
            if len(present) == 0:
                continue
            
            # Per figli unici: se c'è 1 figlio presente e 1 figlio totale, OK
            # Per più figli: richiedi che tutti siano presenti
            if len(siblings) > 1 and len(present) != len(siblings):
               continue

            cost = sum(tree.nodes[sibling_id].total_weight for sibling_id in present)
            
            if cost < best_cost:
                best_cost = cost
                best_group = present  # Usa 'present' invece di 'siblings'
                best_parent = parent_id

        if best_group is None:
            return None
        return best_group, best_parent, best_cost
    
    def apply_sparse_generalization(self, group: List[str], parent_id: str, axis: str):
        """Applica generalizzazione su entrambe le matrici - funziona anche con gruppi di 1 elemento"""
        if axis == 'columns':
            indices = [self.start_to_idx[h3_id] for h3_id in group]

            # Processa matrice dei pesi
            weights_csc = self.current_matrix_sparse.tocsc()
            combined_weights_col = weights_csc[:, indices].sum(axis=1).A1
            
            # Processa matrice dei conteggi
            counts_csc = self.current_counts_sparse.tocsc()
            combined_counts_col = counts_csc[:, indices].sum(axis=1).A1
            
            # Rimuovi colonne vecchie da entrambe le matrici
            mask = np.ones(weights_csc.shape[1], dtype=bool)
            mask[indices] = False
            weights_reduced = weights_csc[:, mask]
            counts_reduced = counts_csc[:, mask]

            # Aggiungi nuove colonne
            combined_weights_sparse = sp.csr_matrix(combined_weights_col).T
            combined_counts_sparse = sp.csr_matrix(combined_counts_col).T
            
            self.current_matrix_sparse = sp.hstack([weights_reduced, combined_weights_sparse]).tocsr()
            self.current_counts_sparse = sp.hstack([counts_reduced, combined_counts_sparse]).tocsr()

            # Aggiorna mappature
            new_start_to_idx = {}
            new_idx_to_start = {}
            new_idx = 0

            for old_idx, h3_id in self.idx_to_start.items():
                if h3_id not in group:
                    new_start_to_idx[h3_id] = new_idx
                    new_idx_to_start[new_idx] = h3_id
                    new_idx += 1

            new_start_to_idx[parent_id] = new_idx
            new_idx_to_start[new_idx] = parent_id

            self.start_to_idx = new_start_to_idx
            self.idx_to_start = new_idx_to_start

        else:
            # Stesso per le righe
            indices = [self.end_to_idx[h3_id] for h3_id in group]

            # Processa matrice dei pesi
            weights_csr = self.current_matrix_sparse.tocsr()
            combined_weights_row = weights_csr[indices, :].sum(axis=0).A1

            # Processa matrice dei conteggi
            counts_csr = self.current_counts_sparse.tocsr()
            combined_counts_row = counts_csr[indices, :].sum(axis=0).A1

            # Rimuovi righe vecchie da entrambe le matrici
            mask = np.ones(weights_csr.shape[0], dtype=bool)
            mask[indices] = False
            weights_reduced = weights_csr[mask, :]
            counts_reduced = counts_csr[mask, :]

            # Aggiungi nuove righe
            combined_weights_sparse = sp.csr_matrix(combined_weights_row)
            combined_counts_sparse = sp.csr_matrix(combined_counts_row)
            
            self.current_matrix_sparse = sp.vstack([weights_reduced, combined_weights_sparse]).tocsr()
            self.current_counts_sparse = sp.vstack([counts_reduced, combined_counts_sparse]).tocsr()

            # Aggiorna mappature
            new_end_to_idx = {}
            new_idx_to_end = {}
            new_idx = 0

            for old_idx, h3_id in self.idx_to_end.items():
                if h3_id not in group:
                    new_end_to_idx[h3_id] = new_idx
                    new_idx_to_end[new_idx] = h3_id
                    new_idx += 1

            new_end_to_idx[parent_id] = new_idx
            new_idx_to_end[new_idx] = parent_id

            self.end_to_idx = new_end_to_idx
            self.idx_to_end = new_idx_to_end

        # Rimuovi i gruppi generalizzati (funziona anche per gruppi di 1)
        if axis == 'columns':
            self.start_sibling_groups = [
                (sibs, par) for sibs, par in self.start_sibling_groups 
                if not any(s in group for s in sibs)
            ]
        else:
            self.end_sibling_groups = [
                (sibs, par) for sibs, par in self.end_sibling_groups 
                if not any(s in group for s in sibs)
            ]

        # Aggiorna la struttura dei siblings con il nuovo nodo
        if axis == 'columns':
            parent_node = self.tree_start.nodes.get(parent_id)
            if parent_node and parent_node.parent:
                siblings_left = [s for s in parent_node.parent.children.keys() 
                            if s in self.start_to_idx and s != parent_id]
                if len(siblings_left) >= 1:
                    grandparent_id = parent_node.parent.h3_id
                    self.start_sibling_groups.append((siblings_left + [parent_id], grandparent_id))
        else:
            parent_node = self.tree_end.nodes.get(parent_id)
            if parent_node and parent_node.parent:
                siblings_left = [s for s in parent_node.parent.children.keys() 
                            if s in self.end_to_idx and s != parent_id]
                if len(siblings_left) >= 1:
                    grandparent_id = parent_node.parent.h3_id
                    self.end_sibling_groups.append((siblings_left + [parent_id], grandparent_id))
    
    def get_min_value_sparse(self) -> int:
        """Ottiene valore minimo da matrice sparse dei pesi (escludendo zeri)"""
        if self.current_matrix_sparse.nnz == 0:
            return 0
        return self.current_matrix_sparse.data.min()
    
    def run_optimized_generalization(self) -> Tuple[sp.csr_matrix, sp.csr_matrix]:
        """Esegue generalizzazione ottimizzata e restituisce entrambe le matrici"""
        print(f"🚀 Avvio generalizzazione ottimizzata (k={self.k_threshold})")
        print("=" * 60)
        
        start_time = time.time()
        self.initialize_optimized_matrix()
        
        step_count = 0
        self.step_rates = []
        
        while True:
            min_value = self.get_min_value_sparse()
            current_shape = self.current_matrix_sparse.shape
            
            print(f"🔍 Step {step_count+1}: Min={min_value:,}, Shape={current_shape[0]}×{current_shape[1]}, NonZero={self.current_matrix_sparse.nnz:,}")
        
            # Controllo se tutte le celle sono >= k_threshold
            min_after_generalization = self.current_matrix_sparse.data.min() if self.current_matrix_sparse.nnz > 0 else float('inf')
            if min_after_generalization >= self.k_threshold:
                print(f"✅ Tutte le celle >= k ({self.k_threshold}), generalizzazione completata.")
                break
            
            # ⚖️ Calcolo del rapporto originale e bilanciamento dinamico
            if step_count == 0:
                initial_cols = self.current_matrix_sparse.shape[1]
                initial_rows = self.current_matrix_sparse.shape[0]
                self.initial_ratio = initial_cols / initial_rows if initial_rows > 0 else 1.0
                self.tolerance = 0.03  # accetta ±3% deviazione

            current_cols = self.current_matrix_sparse.shape[1]
            current_rows = self.current_matrix_sparse.shape[0]
            current_ratio = current_cols / current_rows if current_rows > 0 else 1.0

            # Calcola deviazione percentuale dal rapporto iniziale
            deviation = (current_ratio - self.initial_ratio) / self.initial_ratio

            # Se fuori tolleranza, forza generalizzazione sul lato dominante
            if deviation > self.tolerance:
                axis = 'columns'  # troppe colonne ⇒ generalizza colonne
            elif deviation < -self.tolerance:
                axis = 'rows'     # troppe righe ⇒ generalizza righe
            else:
                # dentro la tolleranza ⇒ alterna normalmente
                axis = 'columns' if step_count % 2 == 0 else 'rows'
            
            best_gen = self.get_best_generalization_fast(axis)
            if not best_gen:
                # Prova sulla direzione opposta
                fallback_axis = 'rows' if axis == 'columns' else 'columns'
                best_gen = self.get_best_generalization_fast(fallback_axis)
                if best_gen:
                    axis = fallback_axis
                    print(f"🔄 Nessuna generalizzazione per la direzione originale, faccio fallback sulla direzione: {fallback_axis}")
                else:
                    print(f"⚠️ Nessuna generalizzazione possibile né su {axis} né sulla direzione alternativa ({fallback_axis}).")
                    if min_after_generalization < self.k_threshold:
                        print(f"❌ Esistono ancora valori < k ({self.k_threshold}), ma impossibile generalizzare ulteriormente.")
                    break

            group, parent_id, cost = best_gen
            
            # Applica generalizzazione su entrambe le matrici
            self.apply_sparse_generalization(group, parent_id, axis)

            if current_shape[0] <= 50 or current_shape[1] <= 50:
                print("🧾 Matrice pesi corrente (valori interi non-zero):")
                print(self.current_matrix_sparse.toarray().astype(int))
                print("🧾 Matrice conteggi corrente (valori interi non-zero):")
                print(self.current_counts_sparse.toarray().astype(int))
            
            # Registra
            self.generalization_history.append({
                'step': step_count + 1,
                'axis': axis,
                'group_size': len(group),
                'parent': parent_id,
                'cost': cost,
                'min_before': min_value,
                'shape_after': self.current_matrix_sparse.shape
            })
            
            elapsed = time.time() - start_time
            step_rate = step_count / elapsed if elapsed > 0 else 0
            self.step_rates.append(step_rate)
            step_count += 1
            
            # Stampa progresso ogni 10 step
            if step_count % 10 == 0:
                print(f"⏱️ Elapsed: {elapsed:.1f}s, Step rate: {step_rate:.2f} steps/sec")
        
        total_time = time.time() - start_time
        print(f"\n🎯 Generalizzazione completata in {step_count} passi ({total_time:.2f}s)")
        print(f"📐 Matrice finale: {self.current_matrix_sparse.shape}")
        print(f"📊 Threshold da rispettare: {self.k_threshold}")
        print(f"📊 Valore minimo finale (pesi): {self.current_matrix_sparse.data.min() if self.current_matrix_sparse.nnz > 0 else 'N/A'}")
        print(f"📊 Valore massimo finale (pesi): {self.current_matrix_sparse.data.max() if self.current_matrix_sparse.nnz > 0 else 'N/A'}")
        print(f"📊 Valore minimo finale (conteggi): {self.current_counts_sparse.data.min() if self.current_counts_sparse.nnz > 0 else 'N/A'}")
        print(f"📊 Valore massimo finale (conteggi): {self.current_counts_sparse.data.max() if self.current_counts_sparse.nnz > 0 else 'N/A'}")
        print(f"💾 Elementi non-zero: {self.current_matrix_sparse.nnz:,}")
        
        return self.current_matrix_sparse, self.current_counts_sparse

def run_optimized_generalization(od_matrix_df: pd.DataFrame, tree_start, tree_end, k_threshold: int = 10*media_peso):
    """
    Esegue la generalizzazione ottimizzata conservando sia i pesi che i conteggi
    
    Returns:
        Tuple[sp.csr_matrix, sp.csr_matrix, OptimizedH3GeneralizedODMatrix]: 
        (matrice_pesi, matrice_conteggi, generalizer)
    """
    generalizer = OptimizedH3GeneralizedODMatrix(od_matrix_df, tree_start, tree_end, k_threshold)
    sparse_result, counts_result = generalizer.run_optimized_generalization()
    
    return sparse_result, counts_result, generalizer

In [61]:
if mode == "SEX":
    sparse_result_man, counts_result_man, generalizer_man = run_optimized_generalization(od_matrix_man, tree_start_man, tree_end_man, k_threshold=10*media_peso)
    sparse_result_woman, counts_result_woman, generalizer_woman = run_optimized_generalization(od_matrix_woman, tree_start_woman, tree_end_woman, k_threshold=10*media_peso)

elif mode == "AGE":
    sparse_result_10_19, counts_result_10_19, generalizer_10_19 = run_optimized_generalization(od_matrix_10_19, tree_start_10_19, tree_end_10_19, k_threshold=10*media_peso)
    sparse_result_20_29, counts_result_20_29, generalizer_20_29 = run_optimized_generalization(od_matrix_20_29, tree_start_20_29, tree_end_20_29, k_threshold=10*media_peso)
    sparse_result_30_39, counts_result_30_39, generalizer_30_39 = run_optimized_generalization(od_matrix_30_39, tree_start_30_39, tree_end_30_39, k_threshold=10*media_peso)
    sparse_result_40_49, counts_result_40_49, generalizer_40_49 = run_optimized_generalization(od_matrix_40_49, tree_start_40_49, tree_end_40_49, k_threshold=10*media_peso)
    sparse_result_50_59, counts_result_50_59, generalizer_50_59 = run_optimized_generalization(od_matrix_50_59, tree_start_50_59, tree_end_50_59, k_threshold=10*media_peso)
    sparse_result_60_69, counts_result_60_69, generalizer_60_69 = run_optimized_generalization(od_matrix_60_69, tree_start_60_69, tree_end_60_69, k_threshold=10*media_peso)
    sparse_result_over70, counts_result_over70, generalizer_over70 = run_optimized_generalization(od_matrix_over70, tree_start_over70, tree_end_over70, k_threshold=10*media_peso)

elif mode == "PRO_CAT":
    sparse_result_procat_1, counts_result_procat_1, generalizer_procat_1 = run_optimized_generalization(od_matrix_procat_1, tree_start_procat_1, tree_end_procat_1, k_threshold=10*media_peso)
    sparse_result_procat_2, counts_result_procat_2, generalizer_procat_2 = run_optimized_generalization(od_matrix_procat_2, tree_start_procat_2, tree_end_procat_2, k_threshold=10*media_peso)
    sparse_result_procat_3, counts_result_procat_3, generalizer_procat_3 = run_optimized_generalization(od_matrix_procat_3, tree_start_procat_3, tree_end_procat_3, k_threshold=10*media_peso)
    sparse_result_procat_4, counts_result_procat_4, generalizer_procat_4 = run_optimized_generalization(od_matrix_procat_4, tree_start_procat_4, tree_end_procat_4, k_threshold=10*media_peso)
    sparse_result_procat_5, counts_result_procat_5, generalizer_procat_5 = run_optimized_generalization(od_matrix_procat_5, tree_start_procat_5, tree_end_procat_5, k_threshold=10*media_peso)
    sparse_result_procat_6, counts_result_procat_6, generalizer_procat_6 = run_optimized_generalization(od_matrix_procat_6, tree_start_procat_6, tree_end_procat_6, k_threshold=10*media_peso)
    sparse_result_procat_7, counts_result_procat_7, generalizer_procat_7 = run_optimized_generalization(od_matrix_procat_7, tree_start_procat_7, tree_end_procat_7, k_threshold=10*media_peso)
    sparse_result_procat_8, counts_result_procat_8, generalizer_procat_8 = run_optimized_generalization(od_matrix_procat_8, tree_start_procat_8, tree_end_procat_8, k_threshold=10*media_peso)

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

🚀 Avvio generalizzazione ottimizzata (k=26741.6279803896)
🔧 Inizializzazione ottimizzata...
📊 Dati filtrati: 898 celle non-zero su 898
🎯 Esagoni target: 631 origini, 665 destinazioni
🔨 Costruzione matrici sparse...
🧠 Pre-calcolo gruppi siblings...
📋 Trovati 392 gruppi origine, 392 gruppi destinazione
✅ Matrici sparse inizializzate: (665, 631) (898 elementi non-zero)
🔍 Step 1: Min=466.07199148, Shape=665×631, NonZero=898
🔍 Step 2: Min=466.07199148, Shape=665×631, NonZero=898
🔍 Step 3: Min=466.07199148, Shape=665×631, NonZero=898
🔍 Step 4: Min=466.07199148, Shape=665×631, NonZero=898
🔍 Step 5: Min=466.07199148, Shape=665×631, NonZero=898
🔍 Step 6: Min=466.07199148, Shape=665×631, NonZero=898
🔍 Step 7: Min=466.07199148, Shape=665×631, NonZero=898
🔍 Step 8: Min=466.07199148, Shape=665×631, NonZero=898
🔍 Step 9: Min=466.07199148, Shape=665×631, NonZero=898
🔍 Step 10: Min=466.07199148, Shape=665×631, NonZero=898
⏱️ Elapsed: 0.1s, Step rate: 140.37 steps/sec
🔍 Step 11: Min=466.07199148, Shape

In [62]:
import folium
import h3
import pandas as pd
import numpy as np
from typing import Dict, List, Optional, Tuple
import scipy.sparse as sp
from branca.colormap import linear
import json
from folium.plugins import HeatMap
import matplotlib.cm as cm
import matplotlib.colors as mcolors

class H3FoliumVisualizer:
    """
    Classe per visualizzare i risultati della generalizzazione H3 con Folium
    """
    
    def __init__(self, generalizer, center_lat=48.8566, center_lon=2.3522):
        """
        Inizializza il visualizzatore
        
        Args:
            generalizer: Istanza di OptimizedH3GeneralizedODMatrix
            center_lat, center_lon: Coordinate del centro della mappa (default: Torino)
        """
        self.generalizer = generalizer
        self.center_lat = center_lat
        self.center_lon = center_lon
        self.sparse_matrix = generalizer.current_matrix_sparse
        
        # Estrai dati dalla matrice sparse per visualizzazione
        self._extract_visualization_data()
    
    def _extract_visualization_data(self):
        print("📊 Estrazione dati per visualizzazione...")
        coo = self.sparse_matrix.tocoo()

        # Prepara liste di mapping con None per indici mancanti
        list_idx_to_start = [None] * self.sparse_matrix.shape[1]
        for idx, h3_id in self.generalizer.idx_to_start.items():
            list_idx_to_start[idx] = h3_id

        list_idx_to_end = [None] * self.sparse_matrix.shape[0]
        for idx, h3_id in self.generalizer.idx_to_end.items():
            list_idx_to_end[idx] = h3_id

        self.origin_data = {}
        self.destination_data = {}
        self.od_pairs = []

        # Calcola flussi totali per origine
        for start_idx, h3_id in enumerate(list_idx_to_start):
            if h3_id is None:
                continue
            total_flow = self.sparse_matrix[:, start_idx].sum()
            if total_flow > 0:
                self.origin_data[h3_id] = total_flow

        # Calcola flussi totali per destinazione
        for end_idx, h3_id in enumerate(list_idx_to_end):
            if h3_id is None:
                continue
            total_flow = self.sparse_matrix[end_idx, :].sum()
            if total_flow > 0:
                self.destination_data[h3_id] = total_flow

        # Estrai coppie OD
        for i, j, data in zip(coo.row, coo.col, coo.data):
            if data > 0:
                if j < len(list_idx_to_start) and i < len(list_idx_to_end):
                    origin_h3 = list_idx_to_start[j]
                    dest_h3 = list_idx_to_end[i]
                    if origin_h3 is not None and dest_h3 is not None:
                        self.od_pairs.append((origin_h3, dest_h3, data))

        print(f"✅ Estratti {len(self.origin_data)} origini, {len(self.destination_data)} destinazioni, {len(self.od_pairs)} coppie OD")

    def _h3_to_geojson(self, h3_id: str) -> Dict:
        """Converte un esagono H3 in GeoJSON"""
        boundary = h3.cell_to_boundary(h3_id)
        # H3 restituisce (lat, lon), GeoJSON vuole (lon, lat)
        coords = [[[lon, lat] for lat, lon in boundary]]
        
        return {
            "type": "Feature",
            "geometry": {
                "type": "Polygon",
                "coordinates": coords
            },
            "properties": {
                "h3_id": h3_id,
                "resolution": h3.get_resolution(h3_id)
            }
        }
    
    def create_base_map(self, zoom_start=10) -> folium.Map:
        """Crea la mappa base"""
        m = folium.Map(
            location=[self.center_lat, self.center_lon],
            zoom_start=zoom_start,
            tiles='OpenStreetMap'
        )
        
        # Aggiungi controlli layer
        folium.plugins.Fullscreen().add_to(m)
        
        return m
    
    def add_origin_hexagons(self, m: folium.Map, max_hexagons=100, alpha=0.6):
        """Aggiunge gli esagoni di origine alla mappa"""
        print(f"🔵 Aggiunta esagoni origine (max {max_hexagons})...")
        
        # Ordina per flusso e prendi i top
        sorted_origins = sorted(self.origin_data.items(), key=lambda x: x[1], reverse=True)

        # k = self.generalizer.k_threshold
        # sorted_origins = [(h3_id, flow) for h3_id, flow in sorted_origins if flow >= k]

        top_origins = sorted_origins[:max_hexagons]
        
        if not top_origins:
            print("⚠️ Nessun esagono origine da visualizzare")
            return
        
        # Calcola range per normalizzazione colori
        flows = [flow for _, flow in top_origins]
        min_flow, max_flow = min(flows), max(flows)
        
        # Gruppo layer per le origini
        origin_group = folium.FeatureGroup(name=f'Origini (Top {len(top_origins)})', show=True)
        
        for h3_id, flow in top_origins:
            try:
                # Ottieni geometria
                geojson = self._h3_to_geojson(h3_id)
                
                # Calcola intensità colore normalizzata
                if max_flow > min_flow:
                    intensity = (flow - min_flow) / (max_flow - min_flow)
                else:
                    intensity = 1.0
                
                # Usa colori esadecimali invece di rgba per evitare problemi
                # Calcola il blu con intensità variabile
                blue_intensity = int(255 * (0.3 + intensity * 0.7))
                fill_color = f"#{0:02x}{0:02x}{blue_intensity:02x}"
                
                # Aggiungi esagono con style_function semplificata
                folium.GeoJson(
                    geojson,
                    style_function=lambda x: {
                        'fillColor': fill_color,
                        'color': 'darkblue',
                        'weight': 1,
                        'fillOpacity': alpha,
                        'opacity': 0.8
                    },
                    popup=folium.Popup(
                        f"""
                        <b>Origine H3</b><br>
                        ID: {h3_id}<br>
                        Risoluzione: {h3.get_resolution(h3_id)}<br>
                        Flusso totale: {flow:,}<br>
                        Rank: {sorted_origins.index((h3_id, flow)) + 1}
                        """,
                        max_width=200
                    ),
                    tooltip=f"Origine: {flow:,} viaggi"
                ).add_to(origin_group)
                
            except Exception as e:
                print(f"⚠️ Errore nell'aggiungere esagono origine {h3_id}: {e}")
        
        origin_group.add_to(m)
        print(f"✅ Aggiunti {len(top_origins)} esagoni origine")
    
    def add_destination_hexagons(self, m: folium.Map, max_hexagons=100, alpha=0.6):
        """Aggiunge gli esagoni di destinazione alla mappa"""
        print(f"🔴 Aggiunta esagoni destinazione (max {max_hexagons})...")
        
        # Ordina per flusso e prendi i top
        sorted_destinations = sorted(self.destination_data.items(), key=lambda x: x[1], reverse=True)

        # k = self.generalizer.k_threshold
        # sorted_destinations = [(h3_id, flow) for h3_id, flow in sorted_destinations if flow >= k]

        top_destinations = sorted_destinations[:max_hexagons]
        
        if not top_destinations:
            print("⚠️ Nessun esagono destinazione da visualizzare")
            return
        
        # Gruppo layer per le destinazioni
        dest_group = folium.FeatureGroup(name=f'Destinazioni (Top {len(top_destinations)})', show=True)
        
        flows = [flow for _, flow in top_destinations]
        min_flow, max_flow = min(flows), max(flows)
        
        for h3_id, flow in top_destinations:
            try:
                geojson = self._h3_to_geojson(h3_id)
                
                # Calcola intensità colore
                if max_flow > min_flow:
                    intensity = (flow - min_flow) / (max_flow - min_flow)
                else:
                    intensity = 1.0
                
                # Usa colori esadecimali per il rosso
                red_intensity = int(255 * (0.3 + intensity * 0.7))
                fill_color = f"#{red_intensity:02x}{0:02x}{0:02x}"
                
                folium.GeoJson(
                    geojson,
                    style_function=lambda x: {
                        'fillColor': fill_color,
                        'color': 'darkred',
                        'weight': 1,
                        'fillOpacity': alpha,
                        'opacity': 0.8
                    },
                    popup=folium.Popup(
                        f"""
                        <b>Destinazione H3</b><br>
                        ID: {h3_id}<br>
                        Risoluzione: {h3.get_resolution(h3_id)}<br>
                        Flusso totale: {flow:,}<br>
                        Rank: {sorted_destinations.index((h3_id, flow)) + 1}
                        """,
                        max_width=200
                    ),
                    tooltip=f"Destinazione: {flow:,} viaggi"
                ).add_to(dest_group)
                
            except Exception as e:
                print(f"⚠️ Errore nell'aggiungere esagono destinazione {h3_id}: {e}")
        
        dest_group.add_to(m)
        print(f"✅ Aggiunti {len(top_destinations)} esagoni destinazione")

In [63]:
if mode == "SEX":
    visualizer_man = H3FoliumVisualizer(generalizer_man)
    visualizer_woman = H3FoliumVisualizer(generalizer_woman)

    mappa_man = visualizer_man.create_base_map(zoom_start=11)
    mappa_woman = visualizer_man.create_base_map(zoom_start=11)

    visualizer_man.add_origin_hexagons(mappa_man, max_hexagons=14000)
    visualizer_man.add_destination_hexagons(mappa_man, max_hexagons=14000)

    visualizer_woman.add_origin_hexagons(mappa_woman, max_hexagons=14000)
    visualizer_woman.add_destination_hexagons(mappa_woman, max_hexagons=14000)

    folium.LayerControl(collapsed=False).add_to(mappa_man)
    folium.LayerControl(collapsed=False).add_to(mappa_woman)

    display(mappa_man)
    display(mappa_woman)

elif mode == "AGE":
    visualizer_10_19 = H3FoliumVisualizer(generalizer_10_19)
    visualizer_20_29 = H3FoliumVisualizer(generalizer_20_29)
    visualizer_30_39 = H3FoliumVisualizer(generalizer_30_39)
    visualizer_40_49 = H3FoliumVisualizer(generalizer_40_49)
    visualizer_50_59 = H3FoliumVisualizer(generalizer_50_59)
    visualizer_60_69 = H3FoliumVisualizer(generalizer_60_69)
    visualizer_over70 = H3FoliumVisualizer(generalizer_over70)

    mappa_10_19 = visualizer_10_19.create_base_map(zoom_start=11)
    mappa_20_29 = visualizer_20_29.create_base_map(zoom_start=11)
    mappa_30_39 = visualizer_30_39.create_base_map(zoom_start=11)
    mappa_40_49 = visualizer_40_49.create_base_map(zoom_start=11)
    mappa_50_59 = visualizer_50_59.create_base_map(zoom_start=11)
    mappa_60_69 = visualizer_60_69.create_base_map(zoom_start=11)
    mappa_over70 = visualizer_over70.create_base_map(zoom_start=11)

    visualizer_10_19.add_origin_hexagons(mappa_10_19, max_hexagons=14000)
    visualizer_10_19.add_destination_hexagons(mappa_10_19, max_hexagons=14000)
    visualizer_20_29.add_origin_hexagons(mappa_20_29, max_hexagons=14000)
    visualizer_20_29.add_destination_hexagons(mappa_20_29, max_hexagons=14000)
    visualizer_30_39.add_origin_hexagons(mappa_30_39, max_hexagons=14000)
    visualizer_30_39.add_destination_hexagons(mappa_30_39, max_hexagons=14000)
    visualizer_40_49.add_origin_hexagons(mappa_40_49, max_hexagons=14000)
    visualizer_40_49.add_destination_hexagons(mappa_40_49, max_hexagons=14000)
    visualizer_50_59.add_origin_hexagons(mappa_50_59, max_hexagons=14000)
    visualizer_50_59.add_destination_hexagons(mappa_50_59, max_hexagons=14000)
    visualizer_60_69.add_origin_hexagons(mappa_60_69, max_hexagons=14000)
    visualizer_60_69.add_destination_hexagons(mappa_60_69, max_hexagons=14000)
    visualizer_over70.add_origin_hexagons(mappa_over70, max_hexagons=14000)
    visualizer_over70.add_destination_hexagons(mappa_over70, max_hexagons=14000)

    folium.LayerControl(collapsed=False).add_to(mappa_10_19)
    folium.LayerControl(collapsed=False).add_to(mappa_20_29)
    folium.LayerControl(collapsed=False).add_to(mappa_30_39)
    folium.LayerControl(collapsed=False).add_to(mappa_40_49)
    folium.LayerControl(collapsed=False).add_to(mappa_50_59)
    folium.LayerControl(collapsed=False).add_to(mappa_60_69)
    folium.LayerControl(collapsed=False).add_to(mappa_over70)

    display(mappa_10_19)
    display(mappa_20_29)
    display(mappa_30_39)
    display(mappa_40_49)
    display(mappa_50_59)
    display(mappa_60_69)
    display(mappa_over70)

elif mode == "PRO_CAT":
    visualizer_procat_1 = H3FoliumVisualizer(generalizer_procat_1)
    visualizer_procat_2 = H3FoliumVisualizer(generalizer_procat_2)
    visualizer_procat_3 = H3FoliumVisualizer(generalizer_procat_3)
    visualizer_procat_4 = H3FoliumVisualizer(generalizer_procat_4)
    visualizer_procat_5 = H3FoliumVisualizer(generalizer_procat_5)
    visualizer_procat_6 = H3FoliumVisualizer(generalizer_procat_6)
    visualizer_procat_7 = H3FoliumVisualizer(generalizer_procat_7)
    visualizer_procat_8 = H3FoliumVisualizer(generalizer_procat_8)

    mappa_procat_1 = visualizer_procat_1.create_base_map(zoom_start=11)
    mappa_procat_2 = visualizer_procat_2.create_base_map(zoom_start=11)
    mappa_procat_3 = visualizer_procat_3.create_base_map(zoom_start=11)
    mappa_procat_4 = visualizer_procat_4.create_base_map(zoom_start=11)
    mappa_procat_5 = visualizer_procat_5.create_base_map(zoom_start=11)
    mappa_procat_6 = visualizer_procat_6.create_base_map(zoom_start=11)
    mappa_procat_7 = visualizer_procat_7.create_base_map(zoom_start=11)
    mappa_procat_8 = visualizer_procat_8.create_base_map(zoom_start=11)

    visualizer_procat_1.add_origin_hexagons(mappa_procat_1, max_hexagons=14000)
    visualizer_procat_1.add_destination_hexagons(mappa_procat_1, max_hexagons=14000)
    visualizer_procat_2.add_origin_hexagons(mappa_procat_2, max_hexagons=14000)
    visualizer_procat_2.add_destination_hexagons(mappa_procat_2, max_hexagons=14000)
    visualizer_procat_3.add_origin_hexagons(mappa_procat_3, max_hexagons=14000)
    visualizer_procat_3.add_destination_hexagons(mappa_procat_3, max_hexagons=14000)
    visualizer_procat_4.add_origin_hexagons(mappa_procat_4, max_hexagons=14000)
    visualizer_procat_4.add_destination_hexagons(mappa_procat_4, max_hexagons=14000)
    visualizer_procat_5.add_origin_hexagons(mappa_procat_5, max_hexagons=14000)
    visualizer_procat_5.add_destination_hexagons(mappa_procat_5, max_hexagons=14000)
    visualizer_procat_6.add_origin_hexagons(mappa_procat_6, max_hexagons=14000)
    visualizer_procat_6.add_destination_hexagons(mappa_procat_6, max_hexagons=14000)
    visualizer_procat_7.add_origin_hexagons(mappa_procat_7, max_hexagons=14000)
    visualizer_procat_7.add_destination_hexagons(mappa_procat_7, max_hexagons=14000)
    visualizer_procat_8.add_origin_hexagons(mappa_procat_8, max_hexagons=14000)
    visualizer_procat_8.add_destination_hexagons(mappa_procat_8, max_hexagons=14000)

    folium.LayerControl(collapsed=False).add_to(mappa_procat_1)
    folium.LayerControl(collapsed=False).add_to(mappa_procat_2)
    folium.LayerControl(collapsed=False).add_to(mappa_procat_3)
    folium.LayerControl(collapsed=False).add_to(mappa_procat_4)
    folium.LayerControl(collapsed=False).add_to(mappa_procat_5)
    folium.LayerControl(collapsed=False).add_to(mappa_procat_6)
    folium.LayerControl(collapsed=False).add_to(mappa_procat_7)
    folium.LayerControl(collapsed=False).add_to(mappa_procat_8)

    display(mappa_procat_1)
    display(mappa_procat_2)
    display(mappa_procat_3)
    display(mappa_procat_4)
    display(mappa_procat_5)
    display(mappa_procat_6)
    display(mappa_procat_7)
    display(mappa_procat_8)

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")

📊 Estrazione dati per visualizzazione...
✅ Estratti 2 origini, 2 destinazioni, 4 coppie OD
📊 Estrazione dati per visualizzazione...
✅ Estratti 2 origini, 2 destinazioni, 4 coppie OD
📊 Estrazione dati per visualizzazione...
✅ Estratti 2 origini, 2 destinazioni, 4 coppie OD
📊 Estrazione dati per visualizzazione...
✅ Estratti 2 origini, 2 destinazioni, 4 coppie OD
📊 Estrazione dati per visualizzazione...
✅ Estratti 2 origini, 2 destinazioni, 4 coppie OD
📊 Estrazione dati per visualizzazione...
✅ Estratti 2 origini, 5 destinazioni, 8 coppie OD
📊 Estrazione dati per visualizzazione...
✅ Estratti 2 origini, 2 destinazioni, 4 coppie OD
📊 Estrazione dati per visualizzazione...
✅ Estratti 2 origini, 2 destinazioni, 4 coppie OD
🔵 Aggiunta esagoni origine (max 14000)...
✅ Aggiunti 2 esagoni origine
🔴 Aggiunta esagoni destinazione (max 14000)...
✅ Aggiunti 2 esagoni destinazione
🔵 Aggiunta esagoni origine (max 14000)...
✅ Aggiunti 2 esagoni origine
🔴 Aggiunta esagoni destinazione (max 14000)...
✅ 

In [64]:
# CALCOLA C_DM e C_AVG
# Equivalence classes sono le coppie origine/destinazione con count >= k
# La loro grandezza è il numero di count nella matrice per qualla coppia righe/colonne
# C_DM : somma dei quadrati delle grandezze delle equivalence classes
# C_AVG : (numero totale di record / numero di equivalence classes) / k

def compute_discernability_and_cavg_sparse(sparse_matrix: sp.csr_matrix, od_matrix, suppressed_count: int, k: int) -> dict:
    
    counts = sparse_matrix.data
    total_records = counts.sum() + suppressed_count
    total_equiv_classes = sparse_matrix.nnz + suppressed_count
    total_records_avg = counts.sum()
    total_equiv_classes_avg = sparse_matrix.nnz

    suppression_penalty = len(od_matrix) * suppressed_count

    # C_DM: somma dei quadrati dei count >= k
    k_anonymous_counts = counts[counts >= k]
    c_dm_gen = (k_anonymous_counts ** 2).sum()
    c_dm = c_dm_gen + suppression_penalty

    # CAVG: ((total_records / total_equiv_classes) / k)    
    c_avg = (total_records_avg / total_equiv_classes_avg) / k if total_equiv_classes_avg > 0 else float('inf')

    return {
        'C_DM': c_dm,
        'C_AVG': c_avg,
        'total_records': total_records,
        'total_equivalence_classes': total_equiv_classes,
        'k': k
    }

if mode == "SEX":
    metrics_man = compute_discernability_and_cavg_sparse(counts_result_man, od_matrix_man, suppressed_count=suppressed_count_man, k=10)
    metrics_woman = compute_discernability_and_cavg_sparse(counts_result_woman, od_matrix_woman, suppressed_count=suppressed_count_woman, k=10)

    print("\n--- SEX ---")
    print(f"Man    → C_DM: {metrics_man['C_DM']:,} | C_AVG: {metrics_man['C_AVG']:.4f}")
    print(f"Woman  → C_DM: {metrics_woman['C_DM']:,} | C_AVG: {metrics_woman['C_AVG']:.4f}")

elif mode == "AGE":
    metrics_10_19 = compute_discernability_and_cavg_sparse(counts_result_10_19, od_matrix_10_19, suppressed_count=suppressed_count_10_19, k=10)
    metrics_20_29 = compute_discernability_and_cavg_sparse(counts_result_20_29, od_matrix_20_29, suppressed_count=suppressed_count_20_29, k=10)
    metrics_30_39 = compute_discernability_and_cavg_sparse(counts_result_30_39, od_matrix_30_39, suppressed_count=suppressed_count_30_39, k=10)
    metrics_40_49 = compute_discernability_and_cavg_sparse(counts_result_40_49, od_matrix_40_49, suppressed_count=suppressed_count_40_49, k=10)
    metrics_50_59 = compute_discernability_and_cavg_sparse(counts_result_50_59, od_matrix_50_59, suppressed_count=suppressed_count_50_59, k=10)
    metrics_60_69 = compute_discernability_and_cavg_sparse(counts_result_60_69, od_matrix_60_69, suppressed_count=suppressed_count_60_69, k=10)
    metrics_over70 = compute_discernability_and_cavg_sparse(counts_result_over70, od_matrix_over70, suppressed_count=suppressed_count_over70, k=10)

    print("\n--- AGE ---")
    print(f"10-19  → C_DM: {metrics_10_19['C_DM']:,} | C_AVG: {metrics_10_19['C_AVG']:.4f}")
    print(f"20-29  → C_DM: {metrics_20_29['C_DM']:,} | C_AVG: {metrics_20_29['C_AVG']:.4f}")
    print(f"30-39  → C_DM: {metrics_30_39['C_DM']:,} | C_AVG: {metrics_30_39['C_AVG']:.4f}")
    print(f"40-49  → C_DM: {metrics_40_49['C_DM']:,} | C_AVG: {metrics_40_49['C_AVG']:.4f}")
    print(f"50-59  → C_DM: {metrics_50_59['C_DM']:,} | C_AVG: {metrics_50_59['C_AVG']:.4f}")
    print(f"60-69  → C_DM: {metrics_60_69['C_DM']:,} | C_AVG: {metrics_60_69['C_AVG']:.4f}")
    print(f"Over70 → C_DM: {metrics_over70['C_DM']:,} | C_AVG: {metrics_over70['C_AVG']:.4f}")

elif mode == "PRO_CAT":
    metrics_procat_1 = compute_discernability_and_cavg_sparse(counts_result_procat_1, od_matrix_procat_1, suppressed_count=suppressed_count_procat_1, k=10)
    metrics_procat_2 = compute_discernability_and_cavg_sparse(counts_result_procat_2, od_matrix_procat_2, suppressed_count=suppressed_count_procat_2, k=10)
    metrics_procat_3 = compute_discernability_and_cavg_sparse(counts_result_procat_3, od_matrix_procat_3, suppressed_count=suppressed_count_procat_3, k=10)
    metrics_procat_4 = compute_discernability_and_cavg_sparse(counts_result_procat_4, od_matrix_procat_4, suppressed_count=suppressed_count_procat_4, k=10)
    metrics_procat_5 = compute_discernability_and_cavg_sparse(counts_result_procat_5, od_matrix_procat_5, suppressed_count=suppressed_count_procat_5, k=10)
    metrics_procat_6 = compute_discernability_and_cavg_sparse(counts_result_procat_6, od_matrix_procat_6, suppressed_count=suppressed_count_procat_6, k=10)
    metrics_procat_7 = compute_discernability_and_cavg_sparse(counts_result_procat_7, od_matrix_procat_7, suppressed_count=suppressed_count_procat_7, k=10)
    metrics_procat_8 = compute_discernability_and_cavg_sparse(counts_result_procat_8, od_matrix_procat_8, suppressed_count=suppressed_count_procat_8, k=10)

    print("\n--- PRO_CAT ---")
    print(f"Cat 1 → C_DM: {metrics_procat_1['C_DM']:,} | C_AVG: {metrics_procat_1['C_AVG']:.4f}")
    print(f"Cat 2 → C_DM: {metrics_procat_2['C_DM']:,} | C_AVG: {metrics_procat_2['C_AVG']:.4f}")
    print(f"Cat 3 → C_DM: {metrics_procat_3['C_DM']:,} | C_AVG: {metrics_procat_3['C_AVG']:.4f}")
    print(f"Cat 4 → C_DM: {metrics_procat_4['C_DM']:,} | C_AVG: {metrics_procat_4['C_AVG']:.4f}")
    print(f"Cat 5 → C_DM: {metrics_procat_5['C_DM']:,} | C_AVG: {metrics_procat_5['C_AVG']:.4f}")
    print(f"Cat 6 → C_DM: {metrics_procat_6['C_DM']:,} | C_AVG: {metrics_procat_6['C_AVG']:.4f}")
    print(f"Cat 7 → C_DM: {metrics_procat_7['C_DM']:,} | C_AVG: {metrics_procat_7['C_AVG']:.4f}")
    print(f"Cat 8 → C_DM: {metrics_procat_8['C_DM']:,} | C_AVG: {metrics_procat_8['C_AVG']:.4f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


--- PRO_CAT ---
Cat 1 → C_DM: 939,368 | C_AVG: 24.6500
Cat 2 → C_DM: 66,447,606 | C_AVG: 219.9000
Cat 3 → C_DM: 12,674,510 | C_AVG: 95.7500
Cat 4 → C_DM: 9,171,727 | C_AVG: 82.6250
Cat 5 → C_DM: 528,596 | C_AVG: 19.0500
Cat 6 → C_DM: 2,669,641 | C_AVG: 34.2375
Cat 7 → C_DM: 12,194,270 | C_AVG: 96.1250
Cat 8 → C_DM: 1,414,522 | C_AVG: 35.0000


In [65]:
from geopy.distance import geodesic
import numpy as np
import pandas as pd
from typing import Dict

def calculate_generalization_distance_metric(df_merged: pd.DataFrame, generalizer, tree_start, tree_end) -> Dict:
    print("🔍 Calcolo metrica di distanza post-generalizzazione...")

    # 1. Ottieni le mappature finali dalla generalizzazione
    final_start_mapping = generalizer.start_to_idx
    final_end_mapping = generalizer.end_to_idx

    # 2. Crea mapping da esagoni originali a esagoni generalizzati
    start_original_to_generalized = {}
    end_original_to_generalized = {}

    unique_start_h3 = df_merged['start_h3'].unique()
    unique_end_h3 = df_merged['end_h3'].unique()

    print(f"📊 Mappatura {len(unique_start_h3)} esagoni origine...")
    for original_h3 in unique_start_h3:
        generalized_h3 = find_generalized_hexagon(original_h3, final_start_mapping, tree_start)
        if generalized_h3:
            start_original_to_generalized[original_h3] = generalized_h3

    print(f"📊 Mappatura {len(unique_end_h3)} esagoni destinazione...")
    for original_h3 in unique_end_h3:
        generalized_h3 = find_generalized_hexagon(original_h3, final_end_mapping, tree_end)
        if generalized_h3:
            end_original_to_generalized[original_h3] = generalized_h3

    # 3. Calcola distanze per le origini
    start_distances, start_coords = [], []
    for _, row in df_merged.iterrows():
        original_h3 = row['start_h3']
        original_coords = (row['start_lat'], row['start_lon'])
        if original_h3 in start_original_to_generalized:
            generalized_h3 = start_original_to_generalized[original_h3]
            generalized_coords = h3.cell_to_latlng(generalized_h3)
            distance = geodesic(original_coords, generalized_coords).meters
            start_distances.append(distance)
            start_coords.append({
                'original_h3': original_h3,
                'generalized_h3': generalized_h3,
                'original_coords': original_coords,
                'generalized_coords': generalized_coords,
                'distance': distance
            })

    # 4. Calcola distanze per le destinazioni
    end_distances, end_coords = [], []
    for _, row in df_merged.iterrows():
        original_h3 = row['end_h3']
        original_coords = (row['end_lat'], row['end_lon'])
        if original_h3 in end_original_to_generalized:
            generalized_h3 = end_original_to_generalized[original_h3]
            generalized_coords = h3.cell_to_latlng(generalized_h3)
            distance = geodesic(original_coords, generalized_coords).meters
            end_distances.append(distance)
            end_coords.append({
                'original_h3': original_h3,
                'generalized_h3': generalized_h3,
                'original_coords': original_coords,
                'generalized_coords': generalized_coords,
                'distance': distance
            })

    # 5. Statistiche
    results = {
        'start_distances': {
            'mean': np.mean(start_distances) if start_distances else 0,
            'median': np.median(start_distances) if start_distances else 0,
            'std': np.std(start_distances) if start_distances else 0,
            'min': np.min(start_distances) if start_distances else 0,
            'max': np.max(start_distances) if start_distances else 0,
            'count': len(start_distances)
        },
        'end_distances': {
            'mean': np.mean(end_distances) if end_distances else 0,
            'median': np.median(end_distances) if end_distances else 0,
            'std': np.std(end_distances) if end_distances else 0,
            'min': np.min(end_distances) if end_distances else 0,
            'max': np.max(end_distances) if end_distances else 0,
            'count': len(end_distances)
        },
        'overall': {
            'mean': np.mean(start_distances + end_distances) if (start_distances or end_distances) else 0,
            'median': np.median(start_distances + end_distances) if (start_distances or end_distances) else 0,
            'std': np.std(start_distances + end_distances) if (start_distances or end_distances) else 0,
            'total_points': len(start_distances) + len(end_distances)
        },
        'mappings': {
            'start_original_to_generalized': start_original_to_generalized,
            'end_original_to_generalized': end_original_to_generalized
        },
        'detailed_coords': {
            'start': start_coords,
            'end': end_coords
        }
    }

    return results


def find_generalized_hexagon(original_h3: str, final_mapping: Dict, tree) -> str:
    if original_h3 in final_mapping:
        return original_h3
    for final_h3 in final_mapping.keys():
        if is_descendant_of(original_h3, final_h3):
            return final_h3
    return None


def is_descendant_of(child_h3: str, parent_h3: str) -> bool:
    child_res = h3.get_resolution(child_h3)
    parent_res = h3.get_resolution(parent_h3)
    if parent_res >= child_res:
        return False
    current = child_h3
    while h3.get_resolution(current) > parent_res:
        current = h3.cell_to_parent(current, h3.get_resolution(current) - 1)
    return current == parent_h3


def analyze_generalization_impact(results: Dict) -> None:
    print("\n" + "-"*60)
    print("📊 ANALISI IMPATTO GENERALIZZAZIONE")
    print("-"*60)

    # Percentili
    all_distances = [c['distance'] for c in results['detailed_coords']['start'] + results['detailed_coords']['end']]
    if all_distances:
        for p in [25, 50, 75, 90, 95, 99]:
            value = np.percentile(all_distances, p)
            print(f"   • {p}° percentile: {value:.2f}m")

    # Per risoluzione
    resolution_analysis = {}
    for coord in results['detailed_coords']['start'] + results['detailed_coords']['end']:
        original_res = h3.get_resolution(coord['original_h3'])
        generalized_res = h3.get_resolution(coord['generalized_h3'])
        key = f"{original_res}→{generalized_res}"
        resolution_analysis.setdefault(key, []).append(coord['distance'])

    print("\n🔍 Analisi per risoluzione:")
    for res_change, distances in resolution_analysis.items():
        mean_dist = np.mean(distances)
        print(f"   • {res_change}: {mean_dist:.2f}m (n={len(distances)})")


def print_category_results(category_name: str, results: Dict) -> None:
    print("\n" + "="*70)
    print(f"📂 Categoria: {category_name}")
    print("="*70)

    o = results['overall']
    print(f"📊 Sintesi: media={o['mean']:.2f}m | mediana={o['median']:.2f}m | punti={o['total_points']:,}")

    s = results['start_distances']
    print(f"\n🎯 Origini:")
    print(f"   • Media: {s['mean']:.2f}m | Mediana: {s['median']:.2f}m | Std: {s['std']:.2f}m")
    print(f"   • Min-Max: {s['min']:.2f}-{s['max']:.2f}m | Punti: {s['count']:,}")

    e = results['end_distances']
    print(f"\n🏁 Destinazioni:")
    print(f"   • Media: {e['mean']:.2f}m | Mediana: {e['median']:.2f}m | Std: {e['std']:.2f}m")
    print(f"   • Min-Max: {e['min']:.2f}-{e['max']:.2f}m | Punti: {e['count']:,}")

    print(f"\n🌍 Complessivo:")
    print(f"   • Media: {o['mean']:.2f}m | Mediana: {o['median']:.2f}m | Std: {o['std']:.2f}m")
    print(f"   • Totale punti: {o['total_points']:,}")


def print_all_results(mode: str, results_dict: Dict[str, Dict]) -> None:
    print("\n" + "#"*80)
    print(f"📑 RISULTATI PER MODALITÀ: {mode}")
    print("#"*80)

    for category, results in results_dict.items():
        print_category_results(category, results)
        analyze_generalization_impact(results)

if mode == "SEX":
    results_dict = {
        "Man": calculate_generalization_distance_metric(filtered_df_man, generalizer_man, tree_start_man, tree_end_man),
        "Woman": calculate_generalization_distance_metric(filtered_df_woman, generalizer_woman, tree_start_woman, tree_end_woman)
    }
    print_all_results("SEX", results_dict)

elif mode == "AGE":
    results_dict = {
        "10-19": calculate_generalization_distance_metric(filtered_df_10_19, generalizer_10_19, tree_start_10_19, tree_end_10_19),
        "20-29": calculate_generalization_distance_metric(filtered_df_20_29, generalizer_20_29, tree_start_20_29, tree_end_20_29),
        "30-39": calculate_generalization_distance_metric(filtered_df_30_39, generalizer_30_39, tree_start_30_39, tree_end_30_39),
        "40-49": calculate_generalization_distance_metric(filtered_df_40_49, generalizer_40_49, tree_start_40_49, tree_end_40_49),
        "50-59": calculate_generalization_distance_metric(filtered_df_50_59, generalizer_50_59, tree_start_50_59, tree_end_50_59),
        "60-69": calculate_generalization_distance_metric(filtered_df_60_69, generalizer_60_69, tree_start_60_69, tree_end_60_69),
        "70+": calculate_generalization_distance_metric(filtered_df_over70, generalizer_over70, tree_start_over70, tree_end_over70)
    }
    print_all_results("AGE", results_dict)

elif mode == "PRO_CAT":
    results_dict = {
        f"ProCat-{i}": calculate_generalization_distance_metric(
            globals()[f"filtered_df_procat_{i}"],
            globals()[f"generalizer_procat_{i}"],
            globals()[f"tree_start_procat_{i}"],
            globals()[f"tree_end_procat_{i}"]
        )
        for i in range(1, 9)
    }
    print_all_results("PRO_CAT", results_dict)

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


🔍 Calcolo metrica di distanza post-generalizzazione...
📊 Mappatura 631 esagoni origine...
📊 Mappatura 665 esagoni destinazione...
🔍 Calcolo metrica di distanza post-generalizzazione...
📊 Mappatura 3624 esagoni origine...
📊 Mappatura 3625 esagoni destinazione...
🔍 Calcolo metrica di distanza post-generalizzazione...
📊 Mappatura 1949 esagoni origine...
📊 Mappatura 1997 esagoni destinazione...
🔍 Calcolo metrica di distanza post-generalizzazione...
📊 Mappatura 1659 esagoni origine...
📊 Mappatura 1656 esagoni destinazione...
🔍 Calcolo metrica di distanza post-generalizzazione...
📊 Mappatura 529 esagoni origine...
📊 Mappatura 512 esagoni destinazione...
🔍 Calcolo metrica di distanza post-generalizzazione...
📊 Mappatura 1537 esagoni origine...
📊 Mappatura 1590 esagoni destinazione...
🔍 Calcolo metrica di distanza post-generalizzazione...
📊 Mappatura 1920 esagoni origine...
📊 Mappatura 1865 esagoni destinazione...
🔍 Calcolo metrica di distanza post-generalizzazione...
📊 Mappatura 900 esagoni o

In [66]:
### Mean Generalisation Error : per ogni flusso anonimizzato, conta quanti esagoni originali sono inclusi nell'area generalizzata (sia per origine che destinazione)
# 
# PAPER:
# Quando le origini e le destinazioni sono aggregate più o meno allo stesso livello (come di solito accade),
# il valore medio 𝐺 rappresenta circa il doppio del numero di celle (esagoni) coinvolte 
# nell'origine o nella destinazione per ogni flusso generalizzato.
# Un valore di 𝐺 = 2 significa quindi che non è stata effettuata alcuna generalizzazione.

class GeneralizationMetric:
    """
    Ḡ = (1/V+) × Σ(|o| + |d|) × v_{o→d}
    """
        
    def __init__(self, k_threshold: int = 10):
        self.k_threshold = k_threshold
        
    def calculate_generalization_error(self, generalized_matrix: sp.csr_matrix, generalizer: 'OptimizedH3GeneralizedODMatrix') -> float:
                
        matrix_dense = generalized_matrix.toarray()
        return self._calculate_dense(matrix_dense, generalizer)
    
    def _calculate_dense(self, matrix: np.ndarray, generalizer) -> float:
        
        # Denominatore sommatoria dei flussi >= k (V+)
        total_volume_anonymous = 0  
        # Numeratore (Σ(|o| + |d|) * v_o→d)
        weighted_count_sum = 0
        
        rows, cols = matrix.shape
        
        # Scorriamo la matrice OD
        for i in range(rows):
            for j in range(cols):
                flow_value = matrix[i, j]
                
                # Considera solo i flussi >= k_threshold
                if flow_value >= self.k_threshold:
                    # Ottieni gli ID H3 dalle mappature
                    origin_h3 = generalizer.idx_to_start.get(j)
                    destination_h3 = generalizer.idx_to_end.get(i)
                    
                    if origin_h3 and destination_h3:
                        # '_get_node_count' dice quante celle originali sono state aggregate dentro ciascun nodo H3 generalizzato
                        origin_count = self._get_node_count(origin_h3, generalizer.tree_start)
                        destination_count = self._get_node_count(destination_h3, generalizer.tree_end)
                        
                        # Sommo i count per ottenere V+
                        total_volume_anonymous += flow_value
                        # Calcola il contributo del numeratore
                        weighted_count_sum += (origin_count + destination_count) * flow_value
        
        # Calcola l'errore medio
        if total_volume_anonymous > 0:
            mean_generalization_error = weighted_count_sum / total_volume_anonymous
        else:
            mean_generalization_error = 0.0
            
        return mean_generalization_error
    
    def _get_node_count(self, h3_id: str, tree) -> int:
        """
        Dato un nodo H3 generalizzato, conta quante celle originali (foglie) rappresenta.
        """
        # Caso limite : il nodo non è nell'albero
        if h3_id not in tree.nodes:
            return 0
        
        node = tree.nodes[h3_id]
        
        # Se è una foglia (livello più basso), conta 1 => l'esagono generalizzato rappresenta una cella originale
        if not node.children:
            return 1
        
        # Altrimenti, chiama _count_terminal_nodes per contare tutte le foglie sotto questo nodo
        return self._count_terminal_nodes(node, tree)
    
    def _count_terminal_nodes(self, node, tree) -> int:
        """
        Conta ricorsivamente tutti i nodi terminali sotto un nodo.
        """
        if not node.children:
            return 1
        
        total = 0
        for child_id in node.children:
            if child_id in tree.nodes:
                child_node = tree.nodes[child_id]
                total += self._count_terminal_nodes(child_node, tree)
            
        return total
    
metric = GeneralizationMetric(k_threshold=10)

print("\n" + "="*80)
print(f"📊 RISULTATI MEAN GENERALISATION ERROR (Ḡ) | mode = {mode}")
print("="*80)

if mode == "SEX":
    error_man = metric.calculate_generalization_error(counts_result_man, generalizer_man)
    error_woman = metric.calculate_generalization_error(counts_result_woman, generalizer_woman)

    print(f"👨 Uomini   → Ḡ = {error_man:.3f}")
    print(f"👩 Donne    → Ḡ = {error_woman:.3f}")

elif mode == "AGE":
    age_errors = {
        "10–19": metric.calculate_generalization_error(counts_result_10_19, generalizer_10_19),
        "20–29": metric.calculate_generalization_error(counts_result_20_29, generalizer_20_29),
        "30–39": metric.calculate_generalization_error(counts_result_30_39, generalizer_30_39),
        "40–49": metric.calculate_generalization_error(counts_result_40_49, generalizer_40_49),
        "50–59": metric.calculate_generalization_error(counts_result_50_59, generalizer_50_59),
        "60–69": metric.calculate_generalization_error(counts_result_60_69, generalizer_60_69),
        "70+":   metric.calculate_generalization_error(counts_result_over70, generalizer_over70),
    }

    for age, value in age_errors.items():
        print(f"🎂 Età {age:<5} → Ḡ = {value:.3f}")

elif mode == "PRO_CAT":
    procat_errors = {}
    for i in range(1, 9):
        error = metric.calculate_generalization_error(
            globals()[f"counts_result_procat_{i}"],
            globals()[f"generalizer_procat_{i}"]
        )
        procat_errors[i] = error
        print(f"📦 ProCat-{i:<2} → Ḡ = {error:.3f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


📊 RISULTATI MEAN GENERALISATION ERROR (Ḡ) | mode = PRO_CAT
📦 ProCat-1  → Ḡ = 1149.968
📦 ProCat-2  → Ḡ = 5689.698
📦 ProCat-3  → Ḡ = 3072.969
📦 ProCat-4  → Ḡ = 2548.286
📦 ProCat-5  → Ḡ = 868.940
📦 ProCat-6  → Ḡ = 1648.619
📦 ProCat-7  → Ḡ = 2861.545
📦 ProCat-8  → Ḡ = 1234.726


In [67]:
def get_leaf_descendants(h3_id: str, tree) -> set:
    """
    Ritorna tutti i nodi foglia discendenti di un nodo H3.
    """
    leaves = set()

    def _collect(node_id):
        node = tree.nodes.get(node_id)
        if not node or not node.children:
            leaves.add(node_id)
        else:
            for child_id in node.children:
                _collect(child_id)

    _collect(h3_id)
    return leaves
if mode == "SEX":
    generalizer_man.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_man.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_man)}
    generalizer_man.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_man.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_man)}
    generalizer_man.start_idx_map = {h3: idx for h3, idx in generalizer_man.start_to_idx.items()}
    generalizer_man.end_idx_map = {h3: idx for h3, idx in generalizer_man.end_to_idx.items()}

    generalizer_woman.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_woman.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_woman)}
    generalizer_woman.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_woman.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_woman)}
    generalizer_woman.start_idx_map = {h3: idx for h3, idx in generalizer_woman.start_to_idx.items()}
    generalizer_woman.end_idx_map = {h3: idx for h3, idx in generalizer_woman.end_to_idx.items()}
    
elif mode == "AGE":
    generalizer_10_19.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_10_19.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_10_19)}
    generalizer_10_19.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_10_19.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_10_19)}
    generalizer_10_19.start_idx_map = {h3: idx for h3, idx in generalizer_10_19.start_to_idx.items()}
    generalizer_10_19.end_idx_map = {h3: idx for h3, idx in generalizer_10_19.end_to_idx.items()}

    generalizer_20_29.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_20_29.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_20_29)}
    generalizer_20_29.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_20_29.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_20_29)}
    generalizer_20_29.start_idx_map = {h3: idx for h3, idx in generalizer_20_29.start_to_idx.items()}
    generalizer_20_29.end_idx_map = {h3: idx for h3, idx in generalizer_20_29.end_to_idx.items()}

    generalizer_30_39.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_30_39.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_30_39)}
    generalizer_30_39.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_30_39.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_30_39)}
    generalizer_30_39.start_idx_map = {h3: idx for h3, idx in generalizer_30_39.start_to_idx.items()}
    generalizer_30_39.end_idx_map = {h3: idx for h3, idx in generalizer_30_39.end_to_idx.items()}

    generalizer_40_49.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_40_49.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_40_49)}
    generalizer_40_49.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_40_49.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_40_49)}
    generalizer_40_49.start_idx_map = {h3: idx for h3, idx in generalizer_40_49.start_to_idx.items()}
    generalizer_40_49.end_idx_map = {h3: idx for h3, idx in generalizer_40_49.end_to_idx.items()}

    generalizer_50_59.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_50_59.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_50_59)}
    generalizer_50_59.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_50_59.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_50_59)}
    generalizer_50_59.start_idx_map = {h3: idx for h3, idx in generalizer_50_59.start_to_idx.items()}
    generalizer_50_59.end_idx_map = {h3: idx for h3, idx in generalizer_50_59.end_to_idx.items()}

    generalizer_60_69.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_60_69.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_60_69)}
    generalizer_60_69.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_60_69.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_60_69)}
    generalizer_60_69.start_idx_map = {h3: idx for h3, idx in generalizer_60_69.start_to_idx.items()}
    generalizer_60_69.end_idx_map = {h3: idx for h3, idx in generalizer_60_69.end_to_idx.items()}

    generalizer_over70.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_over70.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_over70)}
    generalizer_over70.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_over70.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_over70)}
    generalizer_over70.start_idx_map = {h3: idx for h3, idx in generalizer_over70.start_to_idx.items()}
    generalizer_over70.end_idx_map = {h3: idx for h3, idx in generalizer_over70.end_to_idx.items()}

elif mode == "PRO_CAT":
    generalizer_procat_1.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_1.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_procat_1)}
    generalizer_procat_1.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_1.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_procat_1)}
    generalizer_procat_1.start_idx_map = {h3: idx for h3, idx in generalizer_procat_1.start_to_idx.items()}
    generalizer_procat_1.end_idx_map = {h3: idx for h3, idx in generalizer_procat_1.end_to_idx.items()}

    generalizer_procat_2.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_2.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_procat_2)}
    generalizer_procat_2.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_2.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_procat_2)}
    generalizer_procat_2.start_idx_map = {h3: idx for h3, idx in generalizer_procat_2.start_to_idx.items()}
    generalizer_procat_2.end_idx_map = {h3: idx for h3, idx in generalizer_procat_2.end_to_idx.items()}

    generalizer_procat_3.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_3.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_procat_3)}
    generalizer_procat_3.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_3.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_procat_3)}
    generalizer_procat_3.start_idx_map = {h3: idx for h3, idx in generalizer_procat_3.start_to_idx.items()}
    generalizer_procat_3.end_idx_map = {h3: idx for h3, idx in generalizer_procat_3.end_to_idx.items()}

    generalizer_procat_4.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_4.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_procat_4)}
    generalizer_procat_4.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_4.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_procat_4)}
    generalizer_procat_4.start_idx_map = {h3: idx for h3, idx in generalizer_procat_4.start_to_idx.items()}
    generalizer_procat_4.end_idx_map = {h3: idx for h3, idx in generalizer_procat_4.end_to_idx.items()}

    generalizer_procat_5.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_5.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_procat_5)}
    generalizer_procat_5.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_5.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_procat_5)}
    generalizer_procat_5.start_idx_map = {h3: idx for h3, idx in generalizer_procat_5.start_to_idx.items()}
    generalizer_procat_5.end_idx_map = {h3: idx for h3, idx in generalizer_procat_5.end_to_idx.items()}

    generalizer_procat_6.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_6.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_procat_6)}
    generalizer_procat_6.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_6.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_procat_6)}
    generalizer_procat_6.start_idx_map = {h3: idx for h3, idx in generalizer_procat_6.start_to_idx.items()}
    generalizer_procat_6.end_idx_map = {h3: idx for h3, idx in generalizer_procat_6.end_to_idx.items()}

    generalizer_procat_7.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_7.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_procat_7)}
    generalizer_procat_7.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_7.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_procat_7)}
    generalizer_procat_7.start_idx_map = {h3: idx for h3, idx in generalizer_procat_7.start_to_idx.items()}
    generalizer_procat_7.end_idx_map = {h3: idx for h3, idx in generalizer_procat_7.end_to_idx.items()}

    generalizer_procat_8.start_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_8.start_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_start_procat_8)}
    generalizer_procat_8.end_generalization_map = {leaf_h3: gen_h3 for gen_h3 in generalizer_procat_8.end_to_idx for leaf_h3 in get_leaf_descendants(gen_h3, tree_end_procat_8)}
    generalizer_procat_8.start_idx_map = {h3: idx for h3, idx in generalizer_procat_8.start_to_idx.items()}
    generalizer_procat_8.end_idx_map = {h3: idx for h3, idx in generalizer_procat_8.end_to_idx.items()}

# Reconstruction loss : differenza assoluta media tra i flussi originali e quelli ricostruiti, normalizzata per il volume totale

def fast_reconstruction_loss(original_od_df: pd.DataFrame,
                                  generalized_matrix: sp.csr_matrix,
                                  generalizer,
                                  tree_start,
                                  tree_end) -> float:
    """
    Calcola la reconstruction loss includendo anche le celle con 0 viaggi.
    E = (1/V) * Σ |ṽ_o→d - v_o→d|
    """

    original_dict = {
        (row['start_h3'], row['end_h3']): row['count']
        for _, row in original_od_df.iterrows()
    }

    total_volume = sum(original_dict.values())
    if total_volume == 0:
        return 0.0

    total_abs_error = 0.0

    # Precomputo foglie per ogni nodo generalizzato
    start_descendants = {gen: get_leaf_descendants(gen, tree_start) for gen in generalizer.start_to_idx}
    end_descendants   = {gen: get_leaf_descendants(gen, tree_end) for gen in generalizer.end_to_idx}

    # Lista di foglie
    start_leaves = [n for n in tree_start.nodes if not tree_start.nodes[n].children]
    end_leaves   = [n for n in tree_end.nodes if not tree_end.nodes[n].children]

    for s, d in itertools.product(start_leaves, end_leaves):
        true_count = original_dict.get((s, d), 0)

        gen_start = generalizer.start_generalization_map.get(s)
        gen_end   = generalizer.end_generalization_map.get(d)

        if gen_start is None or gen_end is None:
            reconstructed_count = 0
        else:
            row_idx = generalizer.end_idx_map.get(gen_end)
            col_idx = generalizer.start_idx_map.get(gen_start)

            if row_idx is None or col_idx is None:
                reconstructed_count = 0
            else:
                gen_count = generalized_matrix[row_idx, col_idx]
                total_combinations = len(start_descendants[gen_start]) * len(end_descendants[gen_end])
                reconstructed_count = gen_count / total_combinations if total_combinations > 0 else 0

        total_abs_error += abs(reconstructed_count - true_count)

    return total_abs_error / total_volume

In [68]:
print("\n" + "="*80)
print(f"📊 RISULTATI RECONSTRUCTION LOSS | mode = {mode}")
print("="*80)

if mode == "SEX":
    loss_man = fast_reconstruction_loss(original_od_df=od_matrix_first_man, generalized_matrix=counts_result_man, generalizer=generalizer_man, tree_start=tree_start_man, tree_end=tree_end_man)
    loss_woman = fast_reconstruction_loss(original_od_df=od_matrix_first_woman, generalized_matrix=counts_result_woman, generalizer=generalizer_woman, tree_start=tree_start_woman, tree_end=tree_end_woman)

    print(f"👨 Uomini   → RL = {loss_man:.6f}")
    print(f"👩 Donne    → RL = {loss_woman:.6f}")

elif mode == "AGE":
    age_losses = {
        "10–19": fast_reconstruction_loss(od_matrix_first_10_19, counts_result_10_19, generalizer_10_19, tree_start=tree_start_10_19, tree_end=tree_end_10_19),
        "20–29": fast_reconstruction_loss(od_matrix_first_20_29, counts_result_20_29, generalizer_20_29, tree_start=tree_start_20_29, tree_end=tree_end_20_29),
        "30–39": fast_reconstruction_loss(od_matrix_first_30_39, counts_result_30_39, generalizer_30_39, tree_start=tree_start_30_39, tree_end=tree_end_30_39),
        "40–49": fast_reconstruction_loss(od_matrix_first_40_49, counts_result_40_49, generalizer_40_49, tree_start=tree_start_40_49, tree_end=tree_end_40_49),
        "50–59": fast_reconstruction_loss(od_matrix_first_50_59, counts_result_50_59, generalizer_50_59, tree_start=tree_start_50_59, tree_end=tree_end_50_59),
        "60–69": fast_reconstruction_loss(od_matrix_first_60_69, counts_result_60_69, generalizer_60_69, tree_start=tree_start_60_69, tree_end=tree_end_60_69),
        "70+":   fast_reconstruction_loss(od_matrix_first_over70, counts_result_over70, generalizer_over70, tree_start=tree_start_over70, tree_end=tree_end_over70),
    }

    for age, value in age_losses.items():
        print(f"🎂 Età {age:<5} → RL = {value:.6f}")

elif mode == "PRO_CAT":
    procat_losses = {}
    for i in range(1, 9):
        loss = fast_reconstruction_loss(
            original_od_df=globals()[f"od_matrix_first_procat_{i}"],
            generalized_matrix=globals()[f"counts_result_procat_{i}"],
            generalizer=globals()[f"generalizer_procat_{i}"],
            tree_start=globals()[f"tree_start_procat_{i}"],
            tree_end=globals()[f"tree_end_procat_{i}"]
        )
        procat_losses[i] = loss
        print(f"📦 ProCat-{i:<2} → RL = {loss:.6f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")



📊 RISULTATI RECONSTRUCTION LOSS | mode = PRO_CAT
📦 ProCat-1  → RL = 1.818905
📦 ProCat-2  → RL = 1.851833
📦 ProCat-3  → RL = 1.836913
📦 ProCat-4  → RL = 1.837099
📦 ProCat-5  → RL = 1.815282
📦 ProCat-6  → RL = 1.829052
📦 ProCat-7  → RL = 1.842071
📦 ProCat-8  → RL = 1.813110


### Metriche con pesi

In [69]:
if mode == "SEX":
    metrics_man = compute_discernability_and_cavg_sparse(sparse_result_man, od_matrix_man, suppressed_count=suppressed_count_man, k=10*media_peso)
    metrics_woman = compute_discernability_and_cavg_sparse(sparse_result_woman, od_matrix_woman, suppressed_count=suppressed_count_woman, k=10*media_peso)

    print("\n--- SEX ---")
    print(f"Man    → C_DM: {metrics_man['C_DM']:,} | C_AVG: {metrics_man['C_AVG']:.4f}")
    print(f"Woman  → C_DM: {metrics_woman['C_DM']:,} | C_AVG: {metrics_woman['C_AVG']:.4f}")

elif mode == "AGE":
    metrics_10_19 = compute_discernability_and_cavg_sparse(sparse_result_10_19, od_matrix_10_19, suppressed_count=suppressed_count_10_19, k=10*media_peso)
    metrics_20_29 = compute_discernability_and_cavg_sparse(sparse_result_20_29, od_matrix_20_29, suppressed_count=suppressed_count_20_29, k=10*media_peso)
    metrics_30_39 = compute_discernability_and_cavg_sparse(sparse_result_30_39, od_matrix_30_39, suppressed_count=suppressed_count_30_39, k=10*media_peso)
    metrics_40_49 = compute_discernability_and_cavg_sparse(sparse_result_40_49, od_matrix_40_49, suppressed_count=suppressed_count_40_49, k=10*media_peso)
    metrics_50_59 = compute_discernability_and_cavg_sparse(sparse_result_50_59, od_matrix_50_59, suppressed_count=suppressed_count_50_59, k=10*media_peso)
    metrics_60_69 = compute_discernability_and_cavg_sparse(sparse_result_60_69, od_matrix_60_69, suppressed_count=suppressed_count_60_69, k=10*media_peso)
    metrics_over70 = compute_discernability_and_cavg_sparse(sparse_result_over70, od_matrix_over70, suppressed_count=suppressed_count_over70, k=10*media_peso)

    print("\n--- AGE ---")
    print(f"10-19  → C_DM: {metrics_10_19['C_DM']:,} | C_AVG: {metrics_10_19['C_AVG']:.4f}")
    print(f"20-29  → C_DM: {metrics_20_29['C_DM']:,} | C_AVG: {metrics_20_29['C_AVG']:.4f}")
    print(f"30-39  → C_DM: {metrics_30_39['C_DM']:,} | C_AVG: {metrics_30_39['C_AVG']:.4f}")
    print(f"40-49  → C_DM: {metrics_40_49['C_DM']:,} | C_AVG: {metrics_40_49['C_AVG']:.4f}")
    print(f"50-59  → C_DM: {metrics_50_59['C_DM']:,} | C_AVG: {metrics_50_59['C_AVG']:.4f}")
    print(f"60-69  → C_DM: {metrics_60_69['C_DM']:,} | C_AVG: {metrics_60_69['C_AVG']:.4f}")
    print(f"Over70 → C_DM: {metrics_over70['C_DM']:,} | C_AVG: {metrics_over70['C_AVG']:.4f}")

elif mode == "PRO_CAT":
    metrics_procat_1 = compute_discernability_and_cavg_sparse(sparse_result_procat_1, od_matrix_procat_1, suppressed_count=suppressed_count_procat_1, k=10*media_peso)
    metrics_procat_2 = compute_discernability_and_cavg_sparse(sparse_result_procat_2, od_matrix_procat_2, suppressed_count=suppressed_count_procat_2, k=10*media_peso)
    metrics_procat_3 = compute_discernability_and_cavg_sparse(sparse_result_procat_3, od_matrix_procat_3, suppressed_count=suppressed_count_procat_3, k=10*media_peso)
    metrics_procat_4 = compute_discernability_and_cavg_sparse(sparse_result_procat_4, od_matrix_procat_4, suppressed_count=suppressed_count_procat_4, k=10*media_peso)
    metrics_procat_5 = compute_discernability_and_cavg_sparse(sparse_result_procat_5, od_matrix_procat_5, suppressed_count=suppressed_count_procat_5, k=10*media_peso)
    metrics_procat_6 = compute_discernability_and_cavg_sparse(sparse_result_procat_6, od_matrix_procat_6, suppressed_count=suppressed_count_procat_6, k=10*media_peso)
    metrics_procat_7 = compute_discernability_and_cavg_sparse(sparse_result_procat_7, od_matrix_procat_7, suppressed_count=suppressed_count_procat_7, k=10*media_peso)
    metrics_procat_8 = compute_discernability_and_cavg_sparse(sparse_result_procat_8, od_matrix_procat_8, suppressed_count=suppressed_count_procat_8, k=10*media_peso)

    print("\n--- PRO_CAT ---")
    print(f"Cat 1 → C_DM: {metrics_procat_1['C_DM']:,} | C_AVG: {metrics_procat_1['C_AVG']:.4f}")
    print(f"Cat 2 → C_DM: {metrics_procat_2['C_DM']:,} | C_AVG: {metrics_procat_2['C_AVG']:.4f}")
    print(f"Cat 3 → C_DM: {metrics_procat_3['C_DM']:,} | C_AVG: {metrics_procat_3['C_AVG']:.4f}")
    print(f"Cat 4 → C_DM: {metrics_procat_4['C_DM']:,} | C_AVG: {metrics_procat_4['C_AVG']:.4f}")
    print(f"Cat 5 → C_DM: {metrics_procat_5['C_DM']:,} | C_AVG: {metrics_procat_5['C_AVG']:.4f}")
    print(f"Cat 6 → C_DM: {metrics_procat_6['C_DM']:,} | C_AVG: {metrics_procat_6['C_AVG']:.4f}")
    print(f"Cat 7 → C_DM: {metrics_procat_7['C_DM']:,} | C_AVG: {metrics_procat_7['C_AVG']:.4f}")
    print(f"Cat 8 → C_DM: {metrics_procat_8['C_DM']:,} | C_AVG: {metrics_procat_8['C_AVG']:.4f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


--- PRO_CAT ---
Cat 1 → C_DM: 4,574,520,474,357.054 | C_AVG: 21.5175
Cat 2 → C_DM: 225,087,914,976,166.9 | C_AVG: 161.1310
Cat 3 → C_DM: 117,053,406,625,115.27 | C_AVG: 115.6992
Cat 4 → C_DM: 144,398,054,359,744.6 | C_AVG: 126.1422
Cat 5 → C_DM: 7,285,291,449,290.381 | C_AVG: 28.3432
Cat 6 → C_DM: 21,612,307,725,908.734 | C_AVG: 42.6598
Cat 7 → C_DM: 66,126,123,752,729.875 | C_AVG: 88.9394
Cat 8 → C_DM: 6,707,708,709,122.791 | C_AVG: 28.9304


In [70]:
metric = GeneralizationMetric(k_threshold=10*media_peso)

print("\n" + "="*80)
print(f"📊 RISULTATI MEAN GENERALISATION ERROR (Ḡ) | mode = {mode}")
print("="*80)

if mode == "SEX":
    error_man = metric.calculate_generalization_error(sparse_result_man, generalizer_man)
    error_woman = metric.calculate_generalization_error(sparse_result_woman, generalizer_woman)

    print(f"👨 Uomini   → Ḡ = {error_man:.3f}")
    print(f"👩 Donne    → Ḡ = {error_woman:.3f}")

elif mode == "AGE":
    age_errors = {
        "10–19": metric.calculate_generalization_error(sparse_result_10_19, generalizer_10_19),
        "20–29": metric.calculate_generalization_error(sparse_result_20_29, generalizer_20_29),
        "30–39": metric.calculate_generalization_error(sparse_result_30_39, generalizer_30_39),
        "40–49": metric.calculate_generalization_error(sparse_result_40_49, generalizer_40_49),
        "50–59": metric.calculate_generalization_error(sparse_result_50_59, generalizer_50_59),
        "60–69": metric.calculate_generalization_error(sparse_result_60_69, generalizer_60_69),
        "70+":   metric.calculate_generalization_error(sparse_result_over70, generalizer_over70),
    }

    for age, value in age_errors.items():
        print(f"🎂 Età {age:<5} → Ḡ = {value:.3f}")

elif mode == "PRO_CAT":
    procat_errors = {}
    for i in range(1, 9):
        error = metric.calculate_generalization_error(
            globals()[f"sparse_result_procat_{i}"],
            globals()[f"generalizer_procat_{i}"]
        )
        procat_errors[i] = error
        print(f"📦 ProCat-{i:<2} → Ḡ = {error:.3f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")


📊 RISULTATI MEAN GENERALISATION ERROR (Ḡ) | mode = PRO_CAT
📦 ProCat-1  → Ḡ = 1146.913
📦 ProCat-2  → Ḡ = 5647.864
📦 ProCat-3  → Ḡ = 3055.476
📦 ProCat-4  → Ḡ = 2599.855
📦 ProCat-5  → Ḡ = 858.272
📦 ProCat-6  → Ḡ = 1618.627
📦 ProCat-7  → Ḡ = 2848.078
📦 ProCat-8  → Ḡ = 1286.425


In [71]:
def fast_reconstruction_loss(original_od_df: pd.DataFrame,
                                  generalized_matrix: sp.csr_matrix,
                                  generalizer,
                                  tree_start,
                                  tree_end) -> float:
    """
    Calcola la reconstruction loss includendo anche le celle con 0 viaggi.
    E = (1/V) * Σ |ṽ_o→d - v_o→d|
    """

    original_dict = {
        (row['start_h3'], row['end_h3']): row['total_weight']
        for _, row in original_od_df.iterrows()
    }

    total_volume = sum(original_dict.values())
    if total_volume == 0:
        return 0.0

    total_abs_error = 0.0

    # Precomputo foglie per ogni nodo generalizzato
    start_descendants = {gen: get_leaf_descendants(gen, tree_start) for gen in generalizer.start_to_idx}
    end_descendants   = {gen: get_leaf_descendants(gen, tree_end) for gen in generalizer.end_to_idx}

    # Lista di foglie
    start_leaves = [n for n in tree_start.nodes if not tree_start.nodes[n].children]
    end_leaves   = [n for n in tree_end.nodes if not tree_end.nodes[n].children]

    for s, d in itertools.product(start_leaves, end_leaves):
        true_count = original_dict.get((s, d), 0)

        gen_start = generalizer.start_generalization_map.get(s)
        gen_end   = generalizer.end_generalization_map.get(d)

        if gen_start is None or gen_end is None:
            reconstructed_count = 0
        else:
            row_idx = generalizer.end_idx_map.get(gen_end)
            col_idx = generalizer.start_idx_map.get(gen_start)

            if row_idx is None or col_idx is None:
                reconstructed_count = 0
            else:
                gen_count = generalized_matrix[row_idx, col_idx]
                total_combinations = len(start_descendants[gen_start]) * len(end_descendants[gen_end])
                reconstructed_count = gen_count / total_combinations if total_combinations > 0 else 0

        total_abs_error += abs(reconstructed_count - true_count)

    return total_abs_error / total_volume

In [72]:
print("\n" + "="*80)
print(f"📊 RISULTATI RECONSTRUCTION LOSS | mode = {mode}")
print("="*80)

if mode == "SEX":
    loss_man = fast_reconstruction_loss(original_od_df=od_matrix_first_man, generalized_matrix=sparse_result_man, generalizer=generalizer_man, tree_start=tree_start_man, tree_end=tree_end_man)
    loss_woman = fast_reconstruction_loss(original_od_df=od_matrix_first_woman, generalized_matrix=sparse_result_woman, generalizer=generalizer_woman, tree_start=tree_start_woman, tree_end=tree_end_woman)

    print(f"👨 Uomini   → RL = {loss_man:.6f}")
    print(f"👩 Donne    → RL = {loss_woman:.6f}")

elif mode == "AGE":
    age_losses = {
        "10–19": fast_reconstruction_loss(od_matrix_first_10_19, sparse_result_10_19, generalizer_10_19, tree_start=tree_start_10_19, tree_end=tree_end_10_19),
        "20–29": fast_reconstruction_loss(od_matrix_first_20_29, sparse_result_20_29, generalizer_20_29, tree_start=tree_start_20_29, tree_end=tree_end_20_29),
        "30–39": fast_reconstruction_loss(od_matrix_first_30_39, sparse_result_30_39, generalizer_30_39, tree_start=tree_start_30_39, tree_end=tree_end_30_39),
        "40–49": fast_reconstruction_loss(od_matrix_first_40_49, sparse_result_40_49, generalizer_40_49, tree_start=tree_start_40_49, tree_end=tree_end_40_49),
        "50–59": fast_reconstruction_loss(od_matrix_first_50_59, sparse_result_50_59, generalizer_50_59, tree_start=tree_start_50_59, tree_end=tree_end_50_59),
        "60–69": fast_reconstruction_loss(od_matrix_first_60_69, sparse_result_60_69, generalizer_60_69, tree_start=tree_start_60_69, tree_end=tree_end_60_69),
        "70+":   fast_reconstruction_loss(od_matrix_first_over70, sparse_result_over70, generalizer_over70, tree_start=tree_start_over70, tree_end=tree_end_over70),
    }

    for age, value in age_losses.items():
        print(f"🎂 Età {age:<5} → RL = {value:.6f}")

elif mode == "PRO_CAT":
    procat_losses = {}
    for i in range(1, 9):
        loss = fast_reconstruction_loss(
            original_od_df=globals()[f"od_matrix_first_procat_{i}"],
            generalized_matrix=globals()[f"sparse_result_procat_{i}"],
            generalizer=globals()[f"generalizer_procat_{i}"],
            tree_start=globals()[f"tree_start_procat_{i}"],
            tree_end=globals()[f"tree_end_procat_{i}"]
        )
        procat_losses[i] = loss
        print(f"📦 ProCat-{i:<2} → RL = {loss:.6f}")

else:
    print("⚠️ Mode non valido: scegli tra 'SEX', 'AGE', 'PRO_CAT'")



📊 RISULTATI RECONSTRUCTION LOSS | mode = PRO_CAT
📦 ProCat-1  → RL = 1.936979
📦 ProCat-2  → RL = 1.921635
📦 ProCat-3  → RL = 1.933535
📦 ProCat-4  → RL = 1.941658
📦 ProCat-5  → RL = 1.952809
📦 ProCat-6  → RL = 1.945653
📦 ProCat-7  → RL = 1.950162
📦 ProCat-8  → RL = 1.948062
